# I) Initial Imports and setups

## 1) Import statements

In [1]:
import nest_asyncio
import asyncio

nest_asyncio.apply()

In [2]:
import os
from dotenv import load_dotenv
load_dotenv(override=True)

True

In [3]:
os.environ.get("OCR_AGENT")

'unstructured.partition.utils.ocr_models.tesseract_ocr.OCRAgentTesseract'

In [4]:
import io
import pickle
import re
import time
import base64
import uuid
import copy
import json
from pydantic import BaseModel
from typing import List, Optional, Dict
from redis import Redis
from collections import defaultdict
from PIL import Image 
from pathlib import PosixPath
from pymongo.mongo_client import MongoClient
from pymongo.server_api import ServerApi
from google.auth.transport.requests import Request
from google.oauth2.credentials import Credentials
from google_auth_oauthlib.flow import InstalledAppFlow
from googleapiclient.discovery import build
from googleapiclient.errors import HttpError
from googleapiclient.http import MediaIoBaseDownload

In [5]:
from llama_index.core.schema import MetadataMode, IndexNode
from llama_index.llms.openai import OpenAI
from llama_index.llms.gemini import Gemini
from llama_index.llms.groq import Groq
from llama_index.llms.ollama import Ollama

from llama_index.core import Settings
from llama_index.core import ServiceContext, set_global_service_context
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.embeddings.huggingface_optimum import OptimumEmbedding
from llama_index.embeddings.fastembed import FastEmbedEmbedding
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.core.node_parser import (
    SentenceWindowNodeParser,
    SimpleNodeParser,
    SentenceSplitter,
    SemanticDoubleMergingSplitterNodeParser,
    LanguageConfig
)

from llama_index.core.node_parser import (
    HierarchicalNodeParser,
    SentenceSplitter,
)

from llama_index.core.extractors import (
    SummaryExtractor,
    QuestionsAnsweredExtractor,
    TitleExtractor,
    KeywordExtractor,
)


# from llama_index.readers.nougat_ocr import PDFNougatOCR
# from llama_index.readers.smart_pdf_loader import SmartPDFLoader
# from llmsherpa.readers import LayoutPDFReader
from llama_index.readers.file import PyMuPDFReader

from llama_index.core import SimpleDirectoryReader
from llama_index.core.postprocessor import MetadataReplacementPostProcessor
from llama_index.core import VectorStoreIndex, SimpleKeywordTableIndex
from llama_index.core.storage.docstore import SimpleDocumentStore
from llama_index.core.ingestion import (
    DocstoreStrategy,
    IngestionPipeline,
    IngestionCache,
)

from llama_index.core import StorageContext, load_index_from_storage

from llama_index.storage.kvstore.redis import RedisKVStore as RedisCache
from llama_index.storage.docstore.redis import RedisDocumentStore
from llama_index.vector_stores.redis import RedisVectorStore
from redisvl.schema import IndexSchema

from llama_index.core.response.notebook_utils import display_source_node
from llama_index.retrievers.bm25 import BM25Retriever
from llama_index.core.query_engine import RetrieverQueryEngine
from llama_index.core import PromptTemplate
from llama_index.core.schema import TextNode, NodeRelationship, RelatedNodeInfo, ImageNode

from llama_index.core.node_parser import get_leaf_nodes, get_root_nodes
from llama_index.core.retrievers import AutoMergingRetriever, QueryFusionRetriever
from llama_index.core.tools import QueryEngineTool, BaseTool, FunctionTool, ToolMetadata
from llama_index.core.agent import ReActAgent

from llama_index.core.readers.base import BaseReader
from llama_index.core.readers.file.base import default_file_metadata_func
from llama_index.core import Document

/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [6]:
from llama_index.core.workflow import (
    Event,
    StartEvent,
    StopEvent,
    Workflow,
    step,
    Context,
)

from llama_index.core.llms import ChatMessage
from llama_index.core.tools import ToolSelection, ToolOutput
from llama_index.core.workflow import Event
from llama_index.core.tools import FunctionTool

from llama_index.core.workflow import Workflow, StartEvent, StopEvent, step
from llama_index.core.memory import ChatMemoryBuffer
from llama_index.core.llms import MessageRole

## 2) Setup environment variables and other configs

In [7]:
SRC_TYPE = "school" # or college

In [8]:
os.environ["OPENAI_API_KEY"] = os.environ.get("OPENAI_API_KEY")
os.environ["GOOGLE_API_KEY"] = os.environ.get("GOOGLE_API_KEY")
os.environ["GROQ_API_KEY"] = os.environ.get("GROQ_API_KEY")

In [9]:
SCOPES = ["https://www.googleapis.com/auth/classroom.courses.readonly",
          "https://www.googleapis.com/auth/classroom.student-submissions.me.readonly",
          "https://www.googleapis.com/auth/classroom.announcements.readonly",
          "https://www.googleapis.com/auth/classroom.courseworkmaterials.readonly",
          "https://www.googleapis.com/auth/drive.readonly",]

In [10]:
def authenticate() :
    creds = None
    if os.path.exists('token.pickle'):
        with open('token.pickle', 'rb') as token:
            print("credentials loaded")
            creds = pickle.load(token)
    # If there are no (valid) credentials available, let the user log in.
    if not creds or not creds.valid:
        if creds and creds.expired and creds.refresh_token:
            creds.refresh(Request())
        else:
            print("verification initiated")
            flow = InstalledAppFlow.from_client_secrets_file(
                'credentials.json', SCOPES)
            creds = flow.run_local_server(port=0)
        # Save the credentials for the next run
        with open('token.pickle', 'wb') as token:
            print("credentials saved")
            pickle.dump(creds, token)

    return creds

In [11]:
try :
    credentials = authentice()
except Exception as exp :
    print(f"Exception: {exp}")
    os.remove("token.pickle")
    credentials = authenticate()

Exception: name 'authentice' is not defined
verification initiated
Please visit this URL to authorize this application: https://accounts.google.com/o/oauth2/auth?response_type=code&client_id=12410155475-nd3gqe62s4ef8usngtrl2optm7gr35mq.apps.googleusercontent.com&redirect_uri=http%3A%2F%2Flocalhost%3A52315%2F&scope=https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fclassroom.courses.readonly+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fclassroom.student-submissions.me.readonly+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fclassroom.announcements.readonly+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fclassroom.courseworkmaterials.readonly+https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.readonly&state=ersFcXW8ceOzwcX80ALB49xW8hiqfy&access_type=offline
credentials saved


In [31]:
classroom_service = build('classroom', 'v1', credentials=credentials)
drive_service = build('drive', 'v3', credentials=credentials)

In [10]:
""" Convert Images to a base64 string
"""
def image_to_base64(image_path) :
    with open(image_path, "rb") as image_file:
        return base64.b64encode(image_file.read()).decode('utf-8')

In [11]:
groq_text_llm = Groq(model="llama3-70b-8192", api_key=os.environ.get("GROQ_API_KEY"))
# groq_text_llm2 = Groq(model="llama3-70b-8192", api_key=os.environ.get("GROQ_API_KEY2"))
# groq_text_llm3 = Groq(model="llama3-70b-8192", api_key=os.environ.get("GROQ_API_KEY3"))
# llms = [groq_text_llm, groq_text_llm2, groq_text_llm3]

In [12]:
Settings.llm = groq_text_llm

In [13]:
res = groq_text_llm.complete("What is the capital of France?")

In [14]:
res.text

'The capital of France is Paris.'

In [15]:
from groq import Groq

groq_client = Groq()

IMG_DESC_PROMPT = (
    'Please describe the image as if you are explaining it to a blind child.'
    '- Use simple and friendly words.'
    '- Describe the scene in detail, including colors, shapes, people, objects, animals, and background.'  
    '- Share the emotions or feelings in the scene, if any.'
    '- Make the description vivid so they can "see" the image in their mind.'
    '- Do not use technical terms or complicated words.'
    '- Be descriptive but keep it concise, as if telling a story.'
    """- **Only provide the description of the image itself. Do not add introductory phrases like "Here's a description..." or closing phrases like "Would you like me to explain more?".**"""
)

def get_multimodal_response(
        client,
        image_str,
        text = IMG_DESC_PROMPT
    ) :
    completion = client.chat.completions.create(
        model="llama-3.2-11b-vision-preview",
        messages=[
            {
                "role": "user",
                "content": [
                    {
                        "type": "text",
                        "text": text
                    },
                    {
                        "type": "image_url",
                        "image_url": {
                            "url": f"data:image/jpeg;base64,{image_str}"
                        }
                    }
                ]
            }
        ],
        max_tokens=1024,
        top_p=1,
        stream=False,
        stop=None,
    )
    
    return completion.choices[0].message

In [16]:
img_str = image_to_base64("./figures/figure-9-28.jpg")
res = get_multimodal_response(
    groq_client,
    img_str
)
print(res.content)

This image depicts a sketch of a man and five children standing in front of an empty white square, seemingly positioned in front of a TV. The man, wearing a light-colored shirt with a collar, has his right arm around the children's shoulders, while the children, all with short hair, stand side by side, holding an object between them.

In the foreground, two tables with a square dish on them and three chairs with the backrests cut out are arranged in front of the man and children. It appears that the object being held by the children is resting on the tables. The background of the image features a subtle gradient, fading from a darker shade at the bottom to a lighter shade at the top.

The overall atmosphere of the image exudes a sense of community and connection, as the man and children appear to be engaged in a shared activity.


# II) Get documents from external sources

## 1) Code to get specific files from all announcements and materials posted in the classroom

In [21]:
if SRC_TYPE == "college" :
    # For my classroom (modules)
    sub_keywords = ["module", "modules"]
else :
    # For school students
    sub_keywords = ["chapter", "chapters"]

In [11]:
def list_courses(service):
    """Fetch and return a list of all courses."""
    courses = []
    page_token = None

    while True:
        response = service.courses().list(pageToken=page_token).execute()
        courses.extend(response.get('courses', []))
        page_token = response.get('nextPageToken', None)
        if not page_token:
            break

    return courses

def list_announcements(service, course_id):
    """Fetch and return a list of announcements for a given course."""
    announcements = []
    page_token = None

    while True:
        response = service.courses().announcements().list(courseId=course_id, pageToken=page_token).execute()
        announcements.extend(response.get('announcements', []))
        page_token = response.get('nextPageToken', None)
        if not page_token:
            break

    return announcements

def list_materials(service, course_id):
    """Fetch and return a list of materials for a given course."""
    materials = []
    page_token = None

    while True:
        response = service.courses().courseWorkMaterials().list(courseId=course_id, pageToken=page_token).execute()
        materials.extend(response.get('courseWorkMaterial', []))
        page_token = response.get('nextPageToken', None)
        if not page_token:
            break

    return materials

def list_drive_files(material):
    """Fetch and return a list of drive files for a given material."""
    drive_files = []

    for item in material.get('materials', []):
        if 'driveFile' in item:
            drive_files.append(item['driveFile']['driveFile'])

    return drive_files

def download_drive_file(service, file_id, file_name):
    """Download a file from Google Drive."""
    print(f"downloading file : {file_name}")
    request = service.files().get_media(fileId=file_id)
    file_io = io.FileIO(file_name, 'wb')
    downloader = MediaIoBaseDownload(file_io, request)

    done = False
    while not done:
        status, done = downloader.next_chunk()
        print(f"Download {file_name} {int(status.progress() * 100)}%.")

def filter_drive_files(drive_file) :
    if "title" in drive_file :
        return drive_file["title"].split(".")[-1].lower() in ("ppt", "pptx", "docx", "pdf")
    else :
        return False
    
def match_substring_case_insensitive(title, announcement, substrings):
    for substring in substrings :
        pattern = re.compile(re.escape(substring), re.IGNORECASE)
        title_match = pattern.search(title)
        announcement_match = pattern.search(announcement)
        if (title_match is not None) or (announcement_match is not None) :
            return True
    return False

def find_any_keyword(text, keywords):
    # Join keywords into a pattern, escaping each for safe literal matching
    pattern = r'\b(' + '|'.join(re.escape(keyword) for keyword in keywords) + r')\b'
    match = re.search(pattern, text, re.IGNORECASE)
    if match:
        # Return the matched keyword
        return match.group(0)
    return None

def find_subject_name(src_subject) :
    subject = find_any_keyword(
        src_subject, ["politics", "history", "geography", "social science"]
    )
    if subject :
        if subject.lower() == "social science" :
            subject = "Politics"
            
        subject = subject.capitalize() + "_(Social_Science)"
    else :
        subject = src_subject
        
    return subject



def main():
    courses = list_courses(classroom_service)
    # counter = 0

    for course in courses:
        print("*"*100)
        print(f"Course: {course['name']}")
        print("-"*100)

        announcements = list_announcements(classroom_service, course['id'])
        all_files = []
        for announcement in announcements:
            drive_files = list_drive_files(announcement)
            drive_files = list(filter(filter_drive_files, drive_files))
            
            for drive_file in drive_files:
                if match_substring_case_insensitive(drive_file["title"], announcement["text"], sub_keywords) :
                    print(f"    Drive File: {drive_file['title']} (ID: {drive_file['id']})")
                    subject = find_subject_name(course["teacherFolder"]["title"])
                    documents.append(
                        {
                            "file_name" : drive_file["title"],
                            "id" : drive_file["id"],
                            "type" : {
                                "type": "announcement",
                                "post_title" : material["title"],
                                "post_description": material["description"]
                            },
                            "course_info" : course["name"],
                            "subject": subject,
                        }
                    )

        print("-"*100)

        materials = list_materials(classroom_service, course['id'])
        for material in materials:
            drive_files = list_drive_files(material)
            drive_files = list(filter(filter_drive_files, drive_files))
            
            for drive_file in drive_files:
                if match_substring_case_insensitive(drive_file["title"], material["title"], sub_keywords) :
                    print(f"    Drive File: {drive_file['title']} (ID: {drive_file['id']})")
                    subject = find_subject_name(course["teacherFolder"]["title"])
                    documents.append(
                        {
                            "file_name" : drive_file["title"],
                            "id" : drive_file["id"],
                            "type" : {
                                "type": "material",
                                "post_title" : material["title"],
                                "post_description": material["description"]
                            },
                            "course_info" : course["name"],
                            "subject": subject,
                        }
                    )
        print("\n"*2)
    return drive_files, courses, material

documents = []
drive_files, courses, material = main()

NameError: name 'classroom_service' is not defined

In [32]:
courses

[{'id': '728086355817',
  'name': '8th Standard Mathematics',
  'ownerId': '107328804339263850474',
  'creationTime': '2024-10-31T16:17:17.212Z',
  'updateTime': '2024-10-31T18:14:20.240Z',
  'enrollmentCode': 'h4p6g3b',
  'courseState': 'ACTIVE',
  'alternateLink': 'https://classroom.google.com/c/NzI4MDg2MzU1ODE3',
  'teacherGroupEmail': 'Mathematics_teachers_f43cb3fc@classroom.google.com',
  'courseGroupEmail': 'Mathematics_4490d89a@classroom.google.com',
  'teacherFolder': {'id': '11kzhxw4g0cNGWMM62Y_3usAGVnoSX7Sop1Bg44uttywC4wp9QxZcA7Zus4i7GxowTPsvPMaC',
   'title': 'Mathematics',
   'alternateLink': 'https://drive.google.com/drive/folders/11kzhxw4g0cNGWMM62Y_3usAGVnoSX7Sop1Bg44uttywC4wp9QxZcA7Zus4i7GxowTPsvPMaC'},
  'guardiansEnabled': False,
  'calendarId': 'classroom110507087840762832011@group.calendar.google.com',
  'gradebookSettings': {'calculationType': 'TOTAL_POINTS',
   'displaySetting': 'HIDE_OVERALL_GRADE'}},
 {'id': '728082874413',
  'name': '8th Standard English',
  'o

## 2) Data Preprocessing

In [33]:
documents_clean = documents[:]
documents_clean

[{'file_name': 'hemh113.pdf',
  'id': '1hnuOPVyRsHyKMWPCbPwGpuje89VvdZso',
  'type': {'type': 'material',
   'post_title': 'Chapter 13',
   'post_description': 'The notes for chapter 13 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics'},
 {'file_name': 'hemh112.pdf',
  'id': '1L0c4N9S1kpfbNmd_8qyV-TUKnlvE4dV4',
  'type': {'type': 'material',
   'post_title': 'Chapter 12',
   'post_description': 'The notes for chapter 12 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics'},
 {'file_name': 'hemh111.pdf',
  'id': '1P7PFHc4SmiCFDIQAjHFhtN8OEGZ-WDZX',
  'type': {'type': 'material',
   'post_title': 'Chapter 11',
   'post_description': 'The notes for chapter 11 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics'},
 {'file_name': 'hemh110.pdf',
  'id': '1mv5Bq4XR6TnUuUg-WSFAxggYi5Gzoa7F',
  'type': {'type': 'material',
   'post_title': 'Chapter 10',
   'post_description

In [34]:
""" Replace all spaces in subject names with _ and add year info
"""
seen = []
for doc in documents_clean :
    doc["subject"] = doc["subject"].replace(" ", "_")

In [35]:
"""List out all the subjects/courses
"""
for doc in documents_clean :
    print(f"Course: {doc['subject']}")

Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: Mathematics
Course: English
Course: English
Course: English
Course: English
Course: English
Course: English
Course: English
Course: English
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: History_(Social_Science)
Course: Geography_(Social_Science)
Course: Geography_(Social_Science)
Course: Geography_(Social_Science)
Course: Geography_(Social_Science)
Course: Geography_(Social_Science)
Course: Politics_(Social_Science)
Course: Politics_(Social_Science)
Course: Politics_(Social_Science)
Course: Politics_(Social_Science)
Course: Politics_(Social_Science)
Cou

### i) My college data

In [47]:
""" Rename courses
"""
# courses_raw = [
#     "101907/EE704C ELECTRIC VEHICLES", "S7 AD(2021-25) Text Mining", "S7 AD 2021-2025 Batch", "Industrial Safety Engineering", "Computer Networks S6AD", "S6 AD(2021-2025) TOPOLOGICAL DATA ANALYSIS", "S6AD", "Machine Learning S6 AD(2021-2025)", "S5 AD - OOPs using JAVA", "S5 AD 2023 Disaster Management", "FUZZY SETS AND NEURAL NETWORKS", "S5 AD - (2021-25) - MANAGEMENT FOR SOFTWARE ENGINEERS", "S5 AD TOPOLOGY ( 2021-2025)", "DWDM,BDA (2021-25)", "Artificial Intelligence S5 AD(2021-2025)", "AD Constitution of India", "DBMS_S4_AD_2021_Admission", "DIP_HONORS_2021_Admission", "DATA VISUALIZATION", "S4 AD GRAPH THEORY", "Sustainable Engineering", "DESIGN & ENGINEERING", "S3- Minor-Basics of Robotics -101908AE304M", "2021-25_S3_AD_Data Structures", "S3 AD Operating Systems 2022", "RSET 2022-23 S3 AD DMS 101903/MA300A", "S2 AI & DS Mathematics", "Semester 2 AI&DS", "S2 AIDS 2021-2025", "RSET S2 AI& DS- PROFESSIONAL COMMUNICATION", "Basics of Civil Engineering 2021S1AI&DS", "RSET-AI&DS-2021 Adm S1", "Engineering Graphics", "2021-22-S1 AIDS- BME(BASICS OF CIVIL & MECHANICAL ENGINEERING)", "RSET S1 AI&DS Linear Algebra & Calculus", ""
# ]

# courses_new = [
#     ""
# ]

for doc in documents_clean :
    if doc["course"] == " TOPOLOGICAL DATA ANALYSIS-I" :
        doc["course"] = "TOPOLOGICAL DATA ANALYSIS".strip()
        doc["semester"] = 6
        doc["course_code"] = "101008/MA600A".strip()
        print(doc)

""" Code for BDA and DMDW exclusively
"""
# for doc in documents_clean :
#     if doc["course"] == "DWDM,BDA (2021-25)" :
#         if (match_substring_case_insensitive(doc["title"], doc["type"]["title"], "BDA") or match_substring_case_insensitive(doc["title"], doc["type"]["title"], "Big Data Analytics") or match_substring_case_insensitive(doc["title"], doc["type"]["title"], "Cassandra")) :
#             doc["course"] = " BIG DATA ANALYTICS".strip()
#             doc["semester"] = 6
#             doc["course_code"] = "101008/IT600C".strip()
#             print(doc)
#         else :
#             doc["course"] = "DATA WAREHOUSING AND DATA MINING".strip()
#             doc["semester"] = 5
#             doc["course_code"] = "101008/IT500C".strip()
#             print(doc)

{'title': 'Module 4 Software Tools for TDA.pdf', 'id': '1x5t23fgV6E7uSjXpsUp0oK2pOO63EgEA', 'type': {'type': 'material', 'title': 'MODULE 4 :  Software Tools for TDA'}, 'course': 'TOPOLOGICAL DATA ANALYSIS', 'semester': 6, 'course_code': '101008/MA600A', 'module': 'Module4(1)'}
{'title': 'Module 2 Persistence.pdf', 'id': '1KEtxLY0sSZOp8dYKl7bJ43DvVJMN0qov', 'type': {'type': 'material', 'title': 'Module 2: Persistence'}, 'course': 'TOPOLOGICAL DATA ANALYSIS', 'semester': 6, 'course_code': '101008/MA600A', 'module': 'Module2(1)'}
{'title': 'Module 1 Introduction to TDA.pdf', 'id': '13iHTV9RuC7lSfnfatiMHDyAEXeuUcAT7', 'type': {'type': 'material', 'title': 'MODULE 1: INTRODUCTION TO TOPOLOGICAL DATA ANALYSIS'}, 'course': 'TOPOLOGICAL DATA ANALYSIS', 'semester': 6, 'course_code': '101008/MA600A', 'module': 'Module1(1)'}


' Code for BDA and DMDW exclusively\n'

In [40]:
""" For my college content
"""
def add_module_info(title, announcement):
    """ Infer module info from accouncement or file name
    """
    mod_patterns = {
        "Module1": ["module1", "module 1", "m1", "m 1", "mod1", "mod 1", "module-1", "module_1", "moduleI", "module I", "mod-1"],
        "Module2": ["module2", "module 2", "m2", "m 2", "mod2", "mod 2", "module-2", "module_2", "moduleII", "module II", "mod-2"],
        "Module3": ["module3", "module 3", "m3", "m 3", "mod3", "mod 3", "module-3", "module_3", "moduleIII", "module III", "mod-3"],
        "Module4": ["module4", "module 4", "m4", "m 4", "mod4", "mod 4", "module-4", "module_4", "moduleIV", "module IV", "mod-4"],
        "Module5": ["module5", "module 5", "m5", "m 5", "mod5", "mod 5", "module-5", "module_5", "moduleV", "module V", "mod-5", "module 6"],
    }
    module_name = "Miscellaneous"
    for mod in mod_patterns :
        for i in mod_patterns[mod] :
            pattern = re.compile(re.escape(i), re.IGNORECASE)
            title_match = pattern.search(title)
            announcement_match = pattern.search(announcement)
            if title_match or announcement_match :
                module_name = mod
                
    return module_name

In [60]:
""" Add module number information
"""

courses = list(set([doc["course_info"] for doc in documents]))

files = {course: {
            "Module1": 0,
            "Module2": 0,
            "Module3": 0,
            "Module4": 0,
            "Module5": 0,
            "Miscellaneous": 0
            } for course in courses
}
for doc in documents_clean :
    course, module = doc["course"], add_module_info(doc["title"], doc["type"]["title"])
    files[course][module] += 1
    doc["module"] = module + "(" + str(files[course][module]) + ")"

In [61]:
""" List all miscellaneous documents
"""
for doc in documents :
    if add_module_info(doc['title'], doc['type']['title']) == "Miscellaneous" :
        print(f"doc_name: {doc['title']}")
#     print(f"doc_name: {doc['title']}   inferred_name: {add_module_info(doc['title'], doc['type']['title'])}")

doc_name: DWDM-Assignment-2.docx
doc_name: DWDM-Modulewise questions.docx
doc_name: QB.pdf
doc_name: dbms_part2.pdf
doc_name: DBMS_PART1.pdf
doc_name: Moudlewise_QuestionBank.pdf


In [85]:
# documents_clean.append(
#     {
#         'title': 'MOD 3 QB.pdf',
#         'id': '1PfqWASB2my0hF1Nw7LDW13G9Ph2hdlau',
#         'type': {'type': 'material', 'title': 'Module III'},
#         'course': 'BIG DATA ANALYTICS',
#         'semester': 6,
#         'course_code': '101008/IT600C',
#         'module': 'Module3(6)'
#     }
# )

### ii) School data

In [36]:
""" For School students
"""
def roman_to_int(roman):
    # Convert Roman numeral to an integer
    total = 0
    prev_value = 0
    for char in reversed(roman.upper()):
        value = roman_numerals.get(char, 0)
        if value < prev_value:
            total -= value
        else:
            total += value
        prev_value = value
    return total

def extract_chapter_number(text):
    # Regular expression to match "chapter" followed by optional space and Arabic or Roman numeral
    match = re.search(r'chapter\s*(\d+|[IVXLCDM]+)', text, re.IGNORECASE)
    if match:
        chapter = match.group(1)
        # Check if the match is a digit (Arabic numeral) or a Roman numeral
        if chapter.isdigit():
            return int(chapter)
        else:
            return roman_to_int(chapter)
    return None

roman_numerals = {
    'I': 1, 'V': 5, 'X': 10, 'L': 50, 'C': 100, 'D': 500, 'M': 1000
}

In [39]:
def add_grade_info(text) :
    # Define regex pattern to match different variations of grade/standard/5th etc.
    pattern = r'\b(?:grade|standard|std)?\s*(\d+)(?:th)?\s*(?:grade|standard|std)?\b'
    
    # Search for the pattern in the text, case insensitive
    match = re.search(pattern, text, re.IGNORECASE)
    
    # If a match is found, extract the grade number and return it as an integer
    if match:
        return int(match.group(1))
    else :
        return None

In [40]:
""" Add module number and grade information
"""

def add_chapter_info(title, announcement) :
    title_cpt_no = extract_chapter_number(title)
    ann_cpt_no = extract_chapter_number(announcement)
    
    if title_cpt_no :
        return title_cpt_no
    elif ann_cpt_no :
        return ann_cpt_no
    else :
        return None

courses = list(set([doc["subject"] for doc in documents]))

files = {
    course: defaultdict(lambda:0) for course in courses
}
for doc in documents_clean :
    course = doc["subject"]
    chapter_no = str(add_chapter_info(doc["type"]["post_title"], doc["type"]["post_description"]))
    if not chapter_no :
        chapter_no = "0"
    files[course][chapter_no] += 1
    if str(files[course][chapter_no]) != "1" :
        doc["chapter"] = f"Chapter{chapter_no}({str(files[course][chapter_no])})"
    else :
        doc["chapter"] = f"Chapter{chapter_no}"
        
    grade = add_grade_info(doc["course_info"])
    if grade :
        doc["grade"] = f"{grade}th Standard"
    else :
        doc["grade"] = "Unknown"

## 3) Serialize documents object

In [41]:
documents_clean

[{'file_name': 'hemh113.pdf',
  'id': '1hnuOPVyRsHyKMWPCbPwGpuje89VvdZso',
  'type': {'type': 'material',
   'post_title': 'Chapter 13',
   'post_description': 'The notes for chapter 13 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter13',
  'grade': '8th Standard'},
 {'file_name': 'hemh112.pdf',
  'id': '1L0c4N9S1kpfbNmd_8qyV-TUKnlvE4dV4',
  'type': {'type': 'material',
   'post_title': 'Chapter 12',
   'post_description': 'The notes for chapter 12 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter12',
  'grade': '8th Standard'},
 {'file_name': 'hemh111.pdf',
  'id': '1P7PFHc4SmiCFDIQAjHFhtN8OEGZ-WDZX',
  'type': {'type': 'material',
   'post_title': 'Chapter 11',
   'post_description': 'The notes for chapter 11 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter11',
  'grade': '8th Standard'}

In [30]:
import pickle
import json

In [31]:
SRC_TYPE

'school'

In [44]:
# with open(f"data_interm_storage/{SRC_TYPE}/documents_cleaned.pickle", "wb") as pfile :
#     pickle.dump(documents_clean, pfile)

In [32]:
with open(f"data_interm_storage/{SRC_TYPE}/documents_cleaned.pickle", "rb") as pfile :
    documents_info = pickle.load(pfile)

In [46]:
""" Dump it into a json file
"""
# with open(f"data_interm_storage/{SRC_TYPE}/documents_cleaned.json", "w") as jfile :
#     json.dump(documents_clean, jfile, indent=4)

In [33]:
""" Load the data from the json file
"""
with open(f"data_interm_storage/{SRC_TYPE}/documents_cleaned.json", "r") as jfile :
    documents_info = json.load(jfile)

In [34]:
documents_info

[{'file_name': 'hemh113.pdf',
  'id': '1hnuOPVyRsHyKMWPCbPwGpuje89VvdZso',
  'type': {'type': 'material',
   'post_title': 'Chapter 13',
   'post_description': 'The notes for chapter 13 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter13',
  'grade': '8th Standard'},
 {'file_name': 'hemh112.pdf',
  'id': '1L0c4N9S1kpfbNmd_8qyV-TUKnlvE4dV4',
  'type': {'type': 'material',
   'post_title': 'Chapter 12',
   'post_description': 'The notes for chapter 12 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter12',
  'grade': '8th Standard'},
 {'file_name': 'hemh111.pdf',
  'id': '1P7PFHc4SmiCFDIQAjHFhtN8OEGZ-WDZX',
  'type': {'type': 'material',
   'post_title': 'Chapter 11',
   'post_description': 'The notes for chapter 11 has been uploaded'},
  'course_info': '8th Standard Mathematics',
  'subject': 'Mathematics',
  'chapter': 'Chapter11',
  'grade': '8th Standard'}

## 4) Download all the docs into their respective course folder

In [183]:
if not os.path.exists("data") :
    os.mkdir("data")
for document in documents :
    try :
        document["course"] = document["course"].replace("/", "_")
        if not os.path.exists(f"data/{document['course']}") :
            os.mkdir(f"data/{document['course']}")
        download_drive_file(drive_service, document['id'], f"data/{document['course']}/{document['title']}")
    except Exception as exp :
        print(exp)

downloading file : data/ELECTRIC VEHICLE-B1/EV M5 Ktunotes.in.pdf
Download data/ELECTRIC VEHICLE-B1/EV M5 Ktunotes.in.pdf 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV M4 Ktunotes.in.pdf
Download data/ELECTRIC VEHICLE-B1/EV M4 Ktunotes.in.pdf 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV - Module III.pptx
Download data/ELECTRIC VEHICLE-B1/EV - Module III.pptx 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV M3 Ktunotes.in.pdf
Download data/ELECTRIC VEHICLE-B1/EV M3 Ktunotes.in.pdf 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV M2 Ktunotes.in.pdf
Download data/ELECTRIC VEHICLE-B1/EV M2 Ktunotes.in.pdf 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV - Module II- Part I.pptx
Download data/ELECTRIC VEHICLE-B1/EV - Module II- Part I.pptx 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV - Module II- Part II.pptx
Download data/ELECTRIC VEHICLE-B1/EV - Module II- Part II.pptx 100%.
downloading file : data/ELECTRIC VEHICLE-B1/EV - Module I- Part II.pptx
Download

Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/national income problems.pdf 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/MODULE 5 NOTES.docx
Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/MODULE 5 NOTES.docx 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/notes.docx
Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/notes.docx 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/module 3-markets.pptx
Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/module 3-markets.pptx 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/Module 4 notes.docx
Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/Module 4 notes.docx 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/BEP PROBLEMS.docx
Download data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/BEP PROBLEMS.docx 100%.
downloading file : data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/basic concepts ,engineering process and industry.pptx
Dow

Download data/BIG DATA ANALYTICS/BDA Mod-5.pdf 100%.
downloading file : data/BIG DATA ANALYTICS/Big Data Analytics-Module3,4 question bank.docx
Download data/BIG DATA ANALYTICS/Big Data Analytics-Module3,4 question bank.docx 100%.
downloading file : data/BIG DATA ANALYTICS/Module-III-BDA.pptx
Download data/BIG DATA ANALYTICS/Module-III-BDA.pptx 100%.
downloading file : data/BIG DATA ANALYTICS/Module-IV-BDA.pptx
Download data/BIG DATA ANALYTICS/Module-IV-BDA.pptx 100%.
downloading file : data/BIG DATA ANALYTICS/BDA Mod3.pdf
Download data/BIG DATA ANALYTICS/BDA Mod3.pdf 100%.
downloading file : data/BIG DATA ANALYTICS/BDA Mod4.pdf
Download data/BIG DATA ANALYTICS/BDA Mod4.pdf 100%.
downloading file : data/BIG DATA ANALYTICS/Big Data Analytics-module-2 Question Bank.docx
Download data/BIG DATA ANALYTICS/Big Data Analytics-module-2 Question Bank.docx 100%.
downloading file : data/BIG DATA ANALYTICS/Module-II-BDA.pptx
Download data/BIG DATA ANALYTICS/Module-II-BDA.pptx 100%.
downloading fil

Download data/CONSTITUTION OF INDIA/Module IV- Chief Minister and Council of Ministers.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/State Legislature.pdf
Download data/CONSTITUTION OF INDIA/State Legislature.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/The High Court.pdf
Download data/CONSTITUTION OF INDIA/The High Court.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/LOK SABHA.pdf
Download data/CONSTITUTION OF INDIA/LOK SABHA.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/PARLIAMENT.pdf
Download data/CONSTITUTION OF INDIA/PARLIAMENT.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/Prime Minister.pdf
Download data/CONSTITUTION OF INDIA/Prime Minister.pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/RAJYA SABHA .pdf
Download data/CONSTITUTION OF INDIA/RAJYA SABHA .pdf 100%.
downloading file : data/CONSTITUTION OF INDIA/RAJYA SABHA.pdf
Download data/CONSTITUTION OF INDIA/RAJYA SABHA.pdf 100%.
downloading file : data/CONSTITUTION OF IND

Download data/SUSTAINABLE ENGINEERING/carbon credit.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/Air pollution and its effects.docx
Download data/SUSTAINABLE ENGINEERING/Air pollution and its effects.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/water polution.docx
Download data/SUSTAINABLE ENGINEERING/water polution.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/greenhouse.docx
Download data/SUSTAINABLE ENGINEERING/greenhouse.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/3R concept in solid waste management.docx
Download data/SUSTAINABLE ENGINEERING/3R concept in solid waste management.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/Clean Air Act.docx
Download data/SUSTAINABLE ENGINEERING/Clean Air Act.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/zero waste.docx
Download data/SUSTAINABLE ENGINEERING/zero waste.docx 100%.
downloading file : data/SUSTAINABLE ENGINEERING/Module 2.ppt
Download data/SUSTAINABLE EN

Download data/Discrete Mathematical Structures/Revision Questions - Module 3.pptx 100%.
downloading file : data/Discrete Mathematical Structures/Module 4 RR & GF.pdf
Download data/Discrete Mathematical Structures/Module 4 RR & GF.pdf 100%.
downloading file : data/Discrete Mathematical Structures/Module 3- Relations and Functions.pdf
Download data/Discrete Mathematical Structures/Module 3- Relations and Functions.pdf 100%.
downloading file : data/Discrete Mathematical Structures/DMS - notes.pdf
Download data/Discrete Mathematical Structures/DMS - notes.pdf 100%.
downloading file : data/Discrete Mathematical Structures/Module 2 Tutorial Questions Answers.pdf
Download data/Discrete Mathematical Structures/Module 2 Tutorial Questions Answers.pdf 100%.
downloading file : data/Discrete Mathematical Structures/BINOMIAL THEOREM.pptx
Download data/Discrete Mathematical Structures/BINOMIAL THEOREM.pptx 100%.
downloading file : data/Discrete Mathematical Structures/Combinations 1.pptx
Download da

Download data/Basics of Civil Engineering/BCE M2.17 ACOUSTIC INSULATING MATERIALS.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M2.18 CONSTRUCTION CHEMICALS.pdf
Download data/Basics of Civil Engineering/BCE M2.18 CONSTRUCTION CHEMICALS.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M2.19 SOIL.pdf
Download data/Basics of Civil Engineering/BCE M2.19 SOIL.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M3.1 SURVEYING.pdf
Download data/Basics of Civil Engineering/BCE M3.1 SURVEYING.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M3.2.2 FOUNDATIONS.pdf
Download data/Basics of Civil Engineering/BCE M3.2.2 FOUNDATIONS.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M3.2.3 MASONRY.pdf
Download data/Basics of Civil Engineering/BCE M3.2.3 MASONRY.pdf 100%.
downloading file : data/Basics of Civil Engineering/BCE M3.2.4 LOAD BEARING AND FRAMED STRUCTURES.pdf
Download data/Basics of Civil Engineering/BCE M3

Download data/Basics of Mechanical Engineering/Module 6.pdf 100%.
downloading file : data/Basics of Mechanical Engineering/Module 5.pdf
Download data/Basics of Mechanical Engineering/Module 5.pdf 100%.
downloading file : data/Basics of Mechanical Engineering/Module 4.pdf
Download data/Basics of Mechanical Engineering/Module 4.pdf 100%.
downloading file : data/LINEAR ALGEBRA AND CALCULUS/MODULE 4 SEQUENCES AND SERIES HANDOUT.pdf
Download data/LINEAR ALGEBRA AND CALCULUS/MODULE 4 SEQUENCES AND SERIES HANDOUT.pdf 100%.
downloading file : data/LINEAR ALGEBRA AND CALCULUS/INFINITE SERIES Notes on 25-1-2022.pdf
Download data/LINEAR ALGEBRA AND CALCULUS/INFINITE SERIES Notes on 25-1-2022.pdf 100%.
downloading file : data/LINEAR ALGEBRA AND CALCULUS/Notes on 31-1-22 Telescopic sum.pdf
Download data/LINEAR ALGEBRA AND CALCULUS/Notes on 31-1-22 Telescopic sum.pdf 100%.
downloading file : data/LINEAR ALGEBRA AND CALCULUS/p-series - Notes on 1-2-2022.pdf
Download data/LINEAR ALGEBRA AND CALCULUS/p

## III) Data Parsing using Unstructured

## 1) Comparing tesseract OCR, default pymupdf and paddle ocr (Not necessary)

In [9]:
from llama_index.readers.file import PyMuPDFReader
pymu_pdf_loader = PyMuPDFReader()

In [20]:
""" Regular ingestions using simple directory reader
"""
documents = SimpleDirectoryReader(
    input_dir="./data_rough",
    file_extractor={
        ".pdf": pymu_pdf_loader,
    },
    recursive=True
).load_data()

VisionEncoderDecoderModel has generative capabilities, as `prepare_inputs_for_generation` is explicitly overwritten. However, it doesn't directly inherit from `GenerationMixin`. From 👉v4.50👈 onwards, `PreTrainedModel` will NOT inherit from `GenerationMixin`, and this model will lose the ability to call `generate` and other related functions.
  - If you're using `trust_remote_code=True`, you can get rid of this warning by loading the model with an auto class. See https://huggingface.co/docs/transformers/en/model_doc/auto#auto-classes
  - If you are the owner of the model architecture code, please modify your model class such that it inherits from `GenerationMixin` (after `PreTrainedModel`, otherwise you'll get an exception).
  - If you are not the owner of the model architecture class, please contact the model code owner to update it.
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/transformers/models/vit/feature_extraction_vit.py:28: FutureWarning: The class ViTFeatureE

In [24]:
for doc in documents :
    print(doc.metadata)

{'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris_hack/ipynb_files/data_rough/BIG DATA ANALYTICS/BDA Mod-5.pdf', 'file_name': 'BDA Mod-5.pdf', 'file_type': 'application/pdf', 'file_size': 874883, 'creation_date': '2024-10-22', 'last_modified_date': '2024-05-13', 'total_pages': 27, 'source': '1'}
{'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris_hack/ipynb_files/data_rough/BIG DATA ANALYTICS/BDA Mod-5.pdf', 'file_name': 'BDA Mod-5.pdf', 'file_type': 'application/pdf', 'file_size': 874883, 'creation_date': '2024-10-22', 'last_modified_date': '2024-05-13', 'total_pages': 27, 'source': '2'}
{'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris_hack/ipynb_files/data_rough/BIG DATA ANALYTICS/BDA Mod-5.pdf', 'file_name': 'BDA Mod-5.pdf', 'file_type': 'application/pdf', 'file_size': 874883, 'creation_date': '2024-10-22', 'last_modified_date': '2024-05-13', 'total_pages': 27, 'source': '3'}
{'fi

In [11]:
""" PyMuPDF
"""
loader = PyMuPDFReader()
documents = loader.load(file_path="./data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf")

In [12]:
""" Note: the text identified is always empty
"""
documents[25]

Document(id_='31c6ef9c-f77b-4bdc-bb3b-47b2e5c05bc7', embedding=None, metadata={'total_pages': 49, 'file_path': './data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf', 'source': '26'}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, text='', mimetype='text/plain', start_char_idx=None, end_char_idx=None, text_template='{metadata_str}\n\n{content}', metadata_template='{key}: {value}', metadata_seperator='\n')

In [20]:
""" Unstructured with Tesseract OCR on written notes
"""
# from unstructured.partition.auto import partition
# elements = partition(filename="./data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf", content_type="application/pdf")

' Tesseract OCR\n'

In [204]:
# print("\n\n".join([str(el) for el in elements]))

|

a aad

r

we Dat< atk stile slm > divaty- (redunders A =) pebbne 3 po pens : ) 8% FaBer-CASTELL

Dieta se SS

INTRODUCTION : Page No. 4

lla DRM Is a Settle mMmMed- tm manage and J a aaa Alla 2) wa) a

[ al CLTz Y ‘a. A MaNAdge De Cu ANd > 0

#% FABER-Cas Date ———_)

Page No, _f. __|| aka Rete sthich ac } i} A - = AamMin | Lema eing dh \ Hs s ‘ Saxtz | y e, léo 2

Krle ts & callectcon. ot -

pyded 20

which are gueuped ___+_athev -faldels aad _-fles-

PTY Tz [| eater Be Brey

= re ase Cte ei

| 1S CPASEe OS) ix

p4 A}

7% FABER-CASTELL Date PageNo. SO prirelen D een ( Sy. adasm atau’ DBM | Basi's File System | DBMS . RUC i ge and Aiganczes the | Satta Af manaatng th | bes hI TEés in o Lnyane medtum - | O4Ta hase ree! al i Lnhin 4 Om Pu ter 23 ier | | | | ; : | AR A HEDUNDAL Neduadan Ca fn De ! n DRM bee Na yedun— ~ I Ferre Om aA a we CY. | a pre A tr [a eae eed | Tl as HOP AND ME daeso' py) e D4 D pravide MChuUP 42nd ie 4 i O R ANd PLiWVE OT Gar t ti t2Cave fa dala even if d a g rs 

In [16]:
""" Unstructured with Paddle OCR on written notes
"""
from unstructured.partition.pdf import partition_pdf
elements = partition_pdf("./data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf", languages=["en"])

In [17]:
elements[20].metadata.__dir__()

['coordinates',
 'filetype',
 'languages',
 'last_modified',
 'page_number',
 '_known_field_names',
 'file_directory',
 'filename',
 '__module__',
 '__annotations__',
 '__doc__',
 'DEBUG_FIELD_NAMES',
 '__init__',
 '__eq__',
 '__getattr__',
 '__setattr__',
 'from_dict',
 'fields',
 'known_fields',
 'to_dict',
 'update',
 '__dict__',
 '__weakref__',
 '__hash__',
 '__new__',
 '__repr__',
 '__str__',
 '__getattribute__',
 '__delattr__',
 '__lt__',
 '__le__',
 '__ne__',
 '__gt__',
 '__ge__',
 '__reduce_ex__',
 '__reduce__',
 '__subclasshook__',
 '__init_subclass__',
 '__format__',
 '__sizeof__',
 '__dir__',
 '__class__']

In [18]:
elements[464].to_dict()

{'type': 'NarrativeText',
 'element_id': '8c9c86f425701b6894ef3ae4034b8832',
 'text': 'xelsyd.Tt is a unique key Tt cannot he Noll',
 'metadata': {'coordinates': {'points': ((177.0, 738.0),
    (177.0, 836.0),
    (1117.0, 836.0),
    (1117.0, 738.0)),
   'system': 'PixelSpace',
   'layout_width': 1581,
   'layout_height': 2339},
  'filetype': 'application/pdf',
  'languages': ['en'],
  'last_modified': '2024-10-20T13:28:17',
  'page_number': 18,
  'parent_id': 'e566395e2c6634b2ccc61cc32a80b0a1',
  'file_directory': './data/DATABASE MANAGEMENT SYSTEMS',
  'filename': 'DBMS_PART1.pdf'}}

In [19]:
""" Join together elements to form documents
"""
text = ""
for element in elements :
    element_dict = element.to_dict()
    if element_dict["type"] == "Title" :
        text += element_dict["text"] + "\n"
    elif element_dict["type"] in ["Footer", "PageNumber"] :
        continue
    elif element_dict["type"] == "ListItem" :
        text += "  -" + element_dict["text"] + "\n"
    elif element_dict["type"] in ["Formula", "Table"] :
        text += "\n" + element_dict["text"] + "\n\n"
    else :
        text += element_dict["text"] + "\n"
        
print(text)

baDBDBI
FABER-CASTELL
COURSE OUTCOMES
databases.
Entety Belationship diagrams.
CO3 ; Model and design solutons for effictently teplesenting and
querying data using relatonal model..
J bu?ysvy puv boxapo? f sanaof 7yf apoqsuowq#QJ
database applications.
C05 : Discuss and csmpare the aspects of Concurreacy Contrl and
Recovesy in Database systems
C06 ; Appseciate the latest tyeods in databases.
Textbooks :
) Database Systems : Models, danguages, Destign cnd Applicaton Programming
Peayson Educaton y 2013.
  -2) Database System Concepts : Silbeischatz, H.F. Koxth, and S. Sudarshan
sthediltan.
Datalo.c-DBDens
FABER-CASTELL
Date
INTRODUCTION
Page No.
in the effrent etnievalcnsetonand deletion f data from the
data base.and slgcaizes the
maroy Mareye
DATABASE MANAGEMENT SYSTEM (DBMS)
A DBMs is a software system that is designed to manage and
organze tata in a stucted manges.lt allouls dsels to create
modify,and queiy a data base as well as manage tbe security and
access contils for that databas

## 2) Setting all the different document parsers using unstructured

In [35]:
from unstructured.partition.pdf import partition_pdf
from unstructured.partition.ppt import partition_ppt
from unstructured.partition.pptx import partition_pptx
from unstructured.partition.doc import partition_doc
from unstructured.partition.docx import partition_docx

In [23]:
""" Do not run. Only for reference
"""
filename = ""
# PDF parser
elements = partition_pdf(filename=filename, languages=["eng"])
# PPT parser
elements = partition_ppt(filename=filename)
# PPTX parser
elements = partition_pptx(filename=filename)
# DOC parser
elements = partition_doc(filename=filename)
# DOCX parser
elements = partition_docx(filename=filename)

### a) Parse through all the documents

In [36]:
def search_docs_by_keys(doc_info, conditions):
    # Filter the list based on the condition for all the key-value pairs
    return [
        doc for doc in doc_info
        if all(key in doc and doc[key].lower() == value.lower() for key, value in conditions.items())
    ]

In [37]:
search_docs_by_keys(documents_info, {"file_name": "hess403.pdf"})#, "course": "INDUSTRIAL SAFETY ENGINEERING"})

[{'file_name': 'hess403.pdf',
  'id': '1eswF41MoYCcDbVWSbe4HEl1wr9CiPgN0',
  'type': {'type': 'material',
   'post_title': 'Chapter 3',
   'post_description': 'The notes for chapter 3 has been uploaded'},
  'course_info': '8th Standard Geography (Social Science)',
  'subject': 'Geography_(Social_Science)',
  'chapter': 'Chapter3',
  'grade': '8th Standard'}]

### b) Find all documents that have been downloaded but dont exist in documents_info

In [21]:
""" Should print nothing
"""
data_dir = "8_grade_texts" # or data
courses = os.listdir(data_dir)
for course in courses :
    documents_ = os.listdir(os.path.join(f"./{data_dir}", course))
    for document in documents_ :
        doc_path = os.path.join(f"./{data_dir}", course, document)
        ret = search_docs_by_keys(documents_info, {"subject": course, "file_name": document})
        if not ret :
            print(doc_path)

In [22]:
""" Testing out function to generate file metadata
"""
default_file_metadata_func("./data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf")

{'file_path': './data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf',
 'file_name': 'DBMS_PART1.pdf',
 'file_type': 'application/pdf',
 'file_size': 72379561,
 'creation_date': '2024-10-20',
 'last_modified_date': '2024-10-20'}

In [23]:
"""
List of all metadata to add to each document:
1) Module/ Chapter info
2) Semester info
3) Course/ Subject info
4) Post title (optional)
5) Page number

List of additional file metadata
'file_path': './data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf',
'file_name': 'DBMS_PART1.pdf',
'file_type': 'application/pdf',
'file_size': 72379561,
'creation_date': '2024-10-20',
'last_modified_date': '2024-10-20'
"""

"\nList of all metadata to add to each document:\n1) Module/ Chapter info\n2) Semester info\n3) Course/ Subject info\n4) Post title (optional)\n5) Page number\n\nList of additional file metadata\n'file_path': './data/DATABASE MANAGEMENT SYSTEMS/DBMS_PART1.pdf',\n'file_name': 'DBMS_PART1.pdf',\n'file_type': 'application/pdf',\n'file_size': 72379561,\n'creation_date': '2024-10-20',\n'last_modified_date': '2024-10-20'\n"

### c) Below code block not important. Just testing out working of load_data in MyPDFReader

In [38]:
""" Remove all image files that have not been identified as true images
"""        
def check_and_delete_image(img_dir, images, figs, max_aspect_ratio=100):
    valid_imgs = list()
    for fig in figs :
        fig_path = os.path.abspath(os.path.join(img_dir, fig))
        # Open the image and get its dimensions
        with Image.open(fig_path) as img:
            width, height = img.size

            # Calculate the aspect ratio
            aspect_ratio = width / height if width > height else height / width

            # Check if the aspect ratio exceeds the maximum allowed
            if aspect_ratio > max_aspect_ratio or fig_path not in images or width < 10 or height < 10 :
                os.remove(fig_path)
            else :
                valid_imgs.append(fig_path)
    return valid_imgs

In [39]:
def filter_valid_images(elements) :
    valid_imgs = list()
    for element in elements :
        try :
            element_dict = element.to_dict()
            if element_dict["type"] == "Image" and len(element_dict["text"].split(" "))<=3 :
                img_path = os.path.abspath(element_dict["metadata"]["image_path"])
                valid_imgs.append(img_path)
        except :
            continue
    
    return valid_imgs
    

In [40]:
def format_text(element_dict) :
    type_ = element_dict["type"]
    doc_text = element_dict["text"]
    text = ""

    if type_ == "Title" :
        text = doc_text + "\n"
    elif type_ in ["Footer", "PageNumber"] :
        pass
    elif type_ == "ListItem" :
        text = "  -" + doc_text + "\n"
    elif type_ in ["Formula", "Table"] :
        text = "\n" + doc_text + "\n\n"
    else :
        text = doc_text + "\n"

    return text

### i) College data

In [197]:
file = "./8_grade_texts/Geography_(Social_Science)/hess403.pdf"

print(f"file: {file}")
elements = partition_pdf(
    file,
    languages=["eng"],
)
# load_data returns a list of Document objects
docs = list()
text = ""
extra_info = dict()
prev_pg_no = elements[0].metadata.page_number

print(elements[0].metadata)
doc_info = search_docs_by_keys(
    documents_info,
    {
        "course": elements[0].metadata.file_directory.split("/")[-1],
        "title": elements[0].metadata.filename
    }
)
extra_info["module"] = doc_info[0]["module"]
extra_info["course"] = doc_info[0]["course"]
extra_info["semester"] = doc_info[0]["semester"]
extra_info["announcement"] = doc_info[0]["type"]["title"]

for element in elements:
    element_dict = element.to_dict()

    if element.metadata.page_number == prev_pg_no :
        # Format data and add to text
        text += format_text(element_dict)
    else :
        extra_info["page_number"] = prev_pg_no
        docs.extend(
            [
                Document(
                    text = text,
                    metadata=extra_info.copy(),
                    excluded_embed_metadata_keys=["announcement"],
                    excluded_llm_metadata_keys=["announcement"]
                )
            ]
        )

        text = ""
        text += format_text(element_dict)
    prev_pg_no = element.metadata.page_number

else :
    extra_info["page_number"] = prev_pg_no
    docs.extend(
        [
            Document(
                text = text,
                metadata=extra_info.copy(),
                excluded_embed_metadata_keys=["announcement"],
                excluded_llm_metadata_keys=["announcement"]
            )
        ]
    )

file: ./8_grade_texts/Geography_(Social_Science)/hess403.pdf


IndexError: list index out of range

### ii) School data

In [57]:
file = "8_grade_texts/mathematics/hemh101.pdf"
IMAGES = list()
img_dir = f"./Static/{uuid.uuid4()}/figures/"

print(f"file: {file}")
elements = partition_pdf(
    file,
    languages=["eng"],
#     extract_images_in_pdf=True,
#     infer_table_structure=True,
    extract_image_block_types=["Image"],
    extract_image_block_output_dir=img_dir
)

# Remove all extra unwanted images
valid_imgs = filter_valid_images(elements)
figs = os.listdir(img_dir)
valid_imgs = check_and_delete_image(img_dir, valid_imgs, figs)
print(f"{len(valid_imgs)} valid images")
# print(valid_imgs)

# load_data returns a list of Document objects
docs = list()
text = ""
extra_info = dict()
prev_pg_no = elements[0].metadata.page_number

doc_info = search_docs_by_keys(
    documents_info,
    {
        "subject": elements[0].metadata.file_directory.split("/")[-1],
        "file_name": elements[0].metadata.filename
    }
)
extra_info["chapter"] = doc_info[0]["chapter"]
extra_info["subject"] = doc_info[0]["subject"]
extra_info["grade"] = doc_info[0]["grade"]
extra_info["post_title"] = doc_info[0]["type"]["post_title"]
extra_info["post_description"] = doc_info[0]["type"]["post_description"]
extra_info["course_info"] = doc_info[0]["course_info"]

# Add file metadata
file_metadata = default_file_metadata_func(file)
for meta in file_metadata :
    extra_info[meta] = file_metadata[meta]
    
for element in elements:
    element_dict = element.to_dict()
#     if element_dict["page_number"] == 1 :
#         print(element_dict)
    # If the element is a true image, add it as a separate document
    if element_dict["type"] == "Image" and os.path.abspath(element_dict["metadata"]["image_path"]) in valid_imgs :
#         print(f"Image: {element_dict['metadata']['image_path']}")
        img_str = image_to_base64(element_dict["metadata"]["image_path"])
#         print("Getting response from multimodal llm")
        img_summary = get_multimodal_response(groq_client, img_str).content
#         print("Got the response.. moving on... \n")
        
        # Add additional metadata
        img_metadata = extra_info.copy()
        img_metadata["page_number"] = element_dict["metadata"]["page_number"]
        img_metadata["doc_type"] = "Image"
        img_metadata["image_path"] = element_dict["metadata"]["image_path"]
        
        docs.append(
            Document(
                text = img_summary,
                metadata=img_metadata,
                excluded_embed_metadata_keys=[
                    "image_path", "doc_type", "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                ],
                excluded_llm_metadata_keys=[
                    "image_path", "doc_type", "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                ],
            )
        )
        

    if element.metadata.page_number == prev_pg_no :
        # Format data and add to text
        text += format_text(element_dict)
    else :
        extra_info["page_number"] = prev_pg_no
        extra_info["doc_type"] = "Text"
        docs.append(
            Document(
                text = text,
                metadata=extra_info.copy(),
                excluded_embed_metadata_keys=[
                    "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                ],
                excluded_llm_metadata_keys=[
                    "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                ],
            )
        )

        text = ""
        text += format_text(element_dict)
    prev_pg_no = element.metadata.page_number

else :
    extra_info["page_number"] = prev_pg_no
    extra_info["doc_type"] = "Text"
    docs.append(
        Document(
            text = text,
            metadata=extra_info.copy(),
            excluded_embed_metadata_keys=[
                "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
            ],
            excluded_llm_metadata_keys=[
                "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
            ],
        )
    )

file: 8_grade_texts/mathematics/hemh101.pdf
13 valid images


In [61]:
file = "8_grade_texts/mathematics/hemh101.pdf"
IMAGES = list()
img_dir = f"./Static/{uuid.uuid4()}/figures/"

print(f"file: {file}")
elements = partition_pdf(
    file,
    languages=["eng"],
#     extract_images_in_pdf=True,
#     infer_table_structure=True,
    extract_image_block_types=["Image"],
    extract_image_block_output_dir=img_dir
)

file: 8_grade_texts/mathematics/hemh101.pdf


In [62]:
for element in elements :
    element_dict = element.to_dict()
    if element_dict["metadata"]["page_number"] == 1 :
        print(element_dict)
        print("*"*100, end="\n\n")

{'type': 'Image', 'element_id': '8039b608504dc8994d2d04b7b7c0bc3b', 'text': 'RATIONAL NUMBERS    1  CHAPTER1  Rational  Numbers  1.1    Introduction  In Mathematics, we frequently come across simple equations to be solved. For example,  x + 2 = 13  the equation  (1)  is solved when x = 11, because this value of x satisfies the given equation. The  solution  11 is a natural number. On the other hand, for the equation  x + 5 = 5  (2)  the solution gives the whole number 0 (zero). If we consider only natural numbers,  equation (2) cannot be solved. To solve equations like (2), we added the number zero to  the collection of natural numbers and obtained the whole numbers. Even whole numbers  will not be sufficient to solve equations of type  x + 18 = 5  (3)  Do you see ‘why’? We require the number –13 which is not a whole number. This  led us to think of integers, (positive and negative). Note that the positive integers  correspond to natural numbers. One may think that we have enough numbe

In [49]:
for doc in docs :
    if doc.metadata["doc_type"] == "Text" :
        print("*"*100)
        print(doc.text)
        print("\n\n")

****************************************************************************************************
RATIONAL NUMBERS    1  CHAPTER1  Rational  Numbers  1.1    Introduction  In Mathematics, we frequently come across simple equations to be solved. For example,  x + 2 = 13  the equation  (1)  is solved when x = 11, because this value of x satisfies the given equation. The  solution  11 is a natural number. On the other hand, for the equation  x + 5 = 5  (2)  the solution gives the whole number 0 (zero). If we consider only natural numbers,  equation (2) cannot be solved. To solve equations like (2), we added the number zero to  the collection of natural numbers and obtained the whole numbers. Even whole numbers  will not be sufficient to solve equations of type  x + 18 = 5  (3)  Do you see ‘why’? We require the number –13 which is not a whole number. This  led us to think of integers, (positive and negative). Note that the positive integers  correspond to natural numbers. One may think t

In [202]:
for doc in docs :
    if doc.metadata["doc_type"] == "Image" :
        print("*"*100)
        print(f"Image: {doc.metadata['image_path']}")
        print(doc.text)

****************************************************************************************************
Image: ./Static/e6b9a1f3-fe68-4f7b-8782-b4ff33dcea85/figures/figure-1-2.jpg
It is a colorful picture of a farm showing a variety of green plants and fruits. There are different types of plants and leaves scattered across the image. One of the leaves has a QR code to scan and get more information. This image captures the lively atmosphere outside, full of growth and life. The yellow background enhances the vibrant colors and details of the farm plants displayed.
****************************************************************************************************
Image: ./Static/e6b9a1f3-fe68-4f7b-8782-b4ff33dcea85/figures/figure-1-3.jpg
The image is an up-close shot of a black and white camera code that is scannable. It contains several codes which make it difficult to read the unique barcode given to guests participating in a sponsored Facebook feed. The unique code could potentially be 

In [61]:
len(IMAGES)

36

In [74]:
docs[0].metadata

{'chapter': 'Chapter2',
 'subject': 'English',
 'grade': '8th Standard',
 'post_title': 'Chapter 2',
 'post_description': 'The notes for chapter 2 has been uploaded',
 'course_info': '8th Standard English',
 'file_path': '8_grade_texts/English/hehd102.pdf',
 'file_name': 'hehd102.pdf',
 'file_type': 'application/pdf',
 'file_size': 1006731,
 'creation_date': '2024-10-31',
 'last_modified_date': '2024-10-31',
 'page_number': 1,
 'doc_type': 'Image',
 'image_path': './Static/d4498715-8034-4d9b-9bcc-d79b2750802b/figures/figure-1-2.jpg'}

In [16]:
doc_info = search_docs_by_keys(
                documents_info,
                {
                    "course": "./data/BIG DATA ANALYTICS".split("/")[-1],
                    "title": "BDA Mod2.pdf"
                }
            )
print(doc_info)

[{'title': 'BDA Mod2.pdf', 'id': '1_5R7xvazGNx_NNcDOLVf-9TlE5zwlnEu', 'type': {'type': 'announcement', 'title': 'BDA Module II ppt is attached.'}, 'course': 'BIG DATA ANALYTICS', 'semester': 6, 'course_code': '101008/IT600C', 'module': 'Module2(3)'}]


## 2) code for custom Document Parsers

### a) custom pdf parser

### i) College data

In [30]:
class MyPDFReader(BaseReader):
    def format_text(self, type_, doc_text) :
        text = ""
        
        if type_ == "Title" :
            text = doc_text + "\n"
        elif type_ in ["Footer", "PageNumber"] :
            pass
        elif type_ == "ListItem" :
            text = "  -" + doc_text + "\n"
        elif type_ in ["Formula", "Table"] :
            text = "\n" + doc_text + "\n\n"
        else :
            text = doc_text + "\n"
        
        return text
        
    
    def load_data(self, file, extra_info=dict()):
        print(f"file: {file}")
        elements = partition_pdf(file.as_posix(), languages=["eng"])
        # load_data returns a list of Document objects
        docs = list()
        text = ""
        extra_info = dict()
        prev_pg_no = elements[0].metadata.page_number
        
        doc_info = search_docs_by_keys(
            documents_info,
            {
                "course": elements[0].metadata.file_directory.split("/")[-1],
                "title": elements[0].metadata.filename
            }
        )
        extra_info["module"] = doc_info[0]["module"]
        extra_info["course"] = doc_info[0]["course"]
        extra_info["semester"] = doc_info[0]["semester"]
        extra_info["announcement"] = doc_info[0]["type"]["title"]
        
        # Add file metadata
        file_metadata = default_file_metadata_func(file)
        for meta in file_metadata :
            if meta == "file_path" :
                extra_info[meta] = file_metadata[meta].as_posix()
            else :
                extra_info[meta] = file_metadata[meta]
        
        for element in elements:
            element_dict = element.to_dict()
            
            if element.metadata.page_number == prev_pg_no :
                # Format data and add to text
                text += self.format_text(element_dict["type"], element_dict["text"])
            else :
                extra_info["page_number"] = prev_pg_no
                docs.append(
                    Document(
                        text = text,
                        metadata=extra_info.copy(),
                        excluded_embed_metadata_keys=[],
                        excluded_llm_metadata_keys=[]
                    )
                )
                
                text = ""
                text += self.format_text(element_dict["type"], element_dict["text"])
            prev_pg_no = element.metadata.page_number
    
        else :
            extra_info["page_number"] = prev_pg_no
            docs.append(
                Document(
                    text = text,
                    metadata=extra_info.copy(),
                    excluded_embed_metadata_keys=[],
                    excluded_llm_metadata_keys=[]
                )
            )
        
        return docs

#### Testing out the pdf parser

In [32]:
docs = SimpleDirectoryReader(
#     input_dir="./data_rough",
    input_files=["./data/MANAGEMENT FOR SOFTWARE ENGINEERS/MSE MODULE-5.pdf"],
    file_extractor={
        ".pdf": MyPDFReader(),
    },
    recursive=True,
).load_data()

file: data/MANAGEMENT FOR SOFTWARE ENGINEERS/MSE MODULE-5.pdf


In [33]:
docs[0]

Document(id_='306177ae-66db-412a-96b9-daf7a837cbb0', embedding=None, metadata={'module': 'Module5(8)', 'course': 'MANAGEMENT FOR SOFTWARE ENGINEERS', 'semester': 5, 'announcement': 'MODULE-5', 'file_path': 'data/MANAGEMENT FOR SOFTWARE ENGINEERS/MSE MODULE-5.pdf', 'file_name': 'MSE MODULE-5.pdf', 'file_type': 'application/pdf', 'file_size': 1578299, 'creation_date': '2024-10-20', 'last_modified_date': '2024-10-20', 'page_number': 1}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={}, text='Module 5\nMonitoring and Control: Creating the framework- Collecting data- Review- Project Termination Review- Visualizing Progress- Gantt Chart, Slip Chart, Timeline. Cost Monitoring- Earned Value Analysis- Getting the project back to target- Change controlSoftware Configurati

In [39]:
from llama_index.readers.file import PyMuPDFReader
pymu_pdf_loader = PyMuPDFReader()

In [41]:
documents = SimpleDirectoryReader(
    input_dir="./data_rough",
    file_extractor={
        ".pdf": pymu_pdf_loader,
    },
    recursive=True
).load_data()

In [59]:
documents[80]

Document(id_='1d11796c-7418-4767-b764-035d110a5cf4', embedding=None, metadata={'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris_hack/ipynb_files/data_rough/MOD 3 QB.pdf', 'file_name': 'MOD 3 QB.pdf', 'file_type': 'application/pdf', 'file_size': 869914, 'creation_date': '2024-07-21', 'last_modified_date': '2024-05-14', 'total_pages': 16, 'source': '3'}, excluded_embed_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], relationships={}, text='\uf0b7 \nHigh throughput parallel processing \n\uf0b7 \nData locality optimization \n \n5. Identify core components of Hadoop framework? \nThe core components of the Hadoop framework include: \n\uf0b7 \nHDFS (Hadoop Distributed File System): This is the storage component that provides \nhigh-throughput access to application 

## 3) Parsing the docs using a Custom generic document parser

In [73]:
""" Optional
"""
from PIL import Image

Image.MAX_IMAGE_PIXELS = None

### i) For college data

In [76]:
""" Custom Document Parser
"""

class CustomDocReader(BaseReader):
    def __init__(self, file_type, *args, **kwargs) :
        super().__init__(*args, **kwargs)
        
        self.file_type = file_type
        self.doc_parser = self.find_doc_parser(file_type)
        
    
    def find_doc_parser(self, file_type) :
        if file_type == ".pdf" :
            return partition_pdf
        
        elif file_type == ".ppt" :
            return partition_ppt
        
        elif file_type == ".pptx" :
            return partition_pptx
        
        elif file_type == ".doc" :
            return partition_doc
        
        elif file_type == ".docx" :
            return partition_docx
        
        
    def format_text(self, type_, doc_text) :
        text = ""
        
        if type_ == "Title" :
            text = doc_text + "\n"
        elif type_ in ["Footer", "PageNumber"] :
            pass
        elif type_ == "ListItem" :
            text = "  -" + doc_text + "\n"
        elif type_ in ["Formula", "Table"] :
            text = "\n" + doc_text + "\n\n"
        else :
            text = doc_text + "\n"
        
        return text
        
    
    def load_data(self, file, extra_info=dict()):
        print(f"file: {file}")
        elements = self.doc_parser(file.as_posix(), languages=["eng"])
        # load_data returns a list of Document objects
        docs = list()
        text = ""
        extra_info = dict()
        prev_pg_no = elements[0].metadata.page_number
        
        doc_info = search_docs_by_keys(
            documents_info,
            {
                "course": elements[0].metadata.file_directory.split("/")[-1],
                "title": elements[0].metadata.filename
            }
        )
        extra_info["module"] = doc_info[0]["module"]
        extra_info["course"] = doc_info[0]["course"]
        extra_info["semester"] = doc_info[0]["semester"]
        extra_info["announcement"] = doc_info[0]["type"]["title"]
        
        # Add file metadata
        file_metadata = default_file_metadata_func(file)
        for meta in file_metadata :
            if meta == "file_path" :
                extra_info[meta] = file_metadata[meta].as_posix()
            else :
                extra_info[meta] = file_metadata[meta]
        
        for element in elements:
            element_dict = element.to_dict()
            
            if element.metadata.page_number == prev_pg_no :
                # Format data and add to text
                text += self.format_text(element_dict["type"], element_dict["text"])
            else :
                extra_info["page_number"] = prev_pg_no
                docs.append(
                    Document(
                        text = text,
                        metadata=extra_info.copy(),
                        excluded_embed_metadata_keys=[
                            "file_path", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                        excluded_llm_metadata_keys=[
                            "file_path", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                    )
                )
                
                text = ""
                text += self.format_text(element_dict["type"], element_dict["text"])
            prev_pg_no = element.metadata.page_number
    
        else :
            extra_info["page_number"] = prev_pg_no
            docs.append(
                Document(
                    text = text,
                    metadata=extra_info.copy(),
                    excluded_embed_metadata_keys=[
                        "file_path", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                    ],
                    excluded_llm_metadata_keys=[
                        "file_path", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                    ],
                )
            )
        print(f"file: {file} has {len(docs)} pages\n")
        return docs

In [20]:
""" Go course by course, parse through the documents within and add to the set of all
parsed documents
"""
courses = os.listdir("data")
all_parsed_docs = list()
course_count = 0

for course in courses :
    course_count += 1
    print("*"*100)
    print(f"Course: {course}")
    
    start_time = time.time()
    cparsed_docs = SimpleDirectoryReader(
        input_dir=os.path.join("./data", course),
        file_extractor={
            ".pdf": CustomDocReader(".pdf"),
            ".doc": CustomDocReader(".doc"),
            ".ppt": CustomDocReader(".ppt"),
            ".docx": CustomDocReader(".docx"),
            ".pptx": CustomDocReader(".pptx"),
        },
        recursive=True
    ).load_data()
    end_time = time.time()
    
    all_parsed_docs.extend(cparsed_docs)
    
    print(f"Total time taken for execution was {(end_time - start_time)}sec")
    print(f"{course_count} courses done!")
    
    print("Sleeping for 2 secs..😴\n\n")
    time.sleep(2)

****************************************************************************************************
Course: TEXT MINING
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1.pptx has 13 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1_ Document_Representation.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1_ Document_Representation.pptx has 23 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1_ Text categorization.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/TEXT MINING/TEXT MINING-Module 1

****************************************************************************************************
Course: INDUSTRIAL ECONOMICS AND FOREIGN TRADE
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/BEP PROBLEMS.docx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/BEP PROBLEMS.docx has 9 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/Cost, Revenue,Shutdown point, Break even- Production notes.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/Cost, Revenue,Shutdown point, Break even- Production notes.pdf has 16 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/INDUSTRIAL ECONOMICS AND FOREIGN TRADE/IEF

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/Module1_Part3.pptx has 17 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/Module1_Part4.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/Module1_Part4.pptx has 22 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/PAC & LASSO &RIDGE.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/PAC & LASSO &RIDGE.pdf has 5 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/SVM,HMM PPT.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MACHINE LEARNING/SVM,HMM PPT.pptx has 43 pages

file: /home/jovanzac/Jovan/OfflineProj

/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py:3368: DecompressionBombWarning: Image size (94080000 pixels) exceeds limit of 89478485 pixels, could be decompression bomb DOS attack.
  warnings.warn(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py:3368: DecompressionBombWarning: Image size (94080000 pixels) exceeds limit of 89478485 pixels, could be decompression bomb DOS attack.
  warnings.warn(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py:3368: DecompressionBombWarning: Image size (94080000 pixels) exceeds limit of 89478485 pixels, could be decompression bomb DOS attack.
  warnings.warn(


file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MANAGEMENT FOR SOFTWARE ENGINEERS/MOD-3-PROBLEMS.pdf has 15 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MANAGEMENT FOR SOFTWARE ENGINEERS/MOD-4-PART-1.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MANAGEMENT FOR SOFTWARE ENGINEERS/MOD-4-PART-1.pdf has 40 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MANAGEMENT FOR SOFTWARE ENGINEERS/MOD-4-PROBLEMS.pdf


...

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.1 STONES.pdf has 55 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.10 GLASS.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.10 GLASS.pdf has 14 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.11 CERAMICS.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.11 CERAMICS.pdf has 16 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M2.12 ALUMINIUM.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M3.2.9 FIRE SAFETY FOR BUILDINGS.pdf has 15 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M3.3 Concepts of sustainable construction.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M3.3 Concepts of sustainable construction.pdf has 46 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M3.4 Components of roads and highways.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/BCE M3.4 Components of roads and highways.pdf has 7 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Civil Engineering/

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Isometric Projections & views #1.pptx has 35 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Isometric Projections & views #2.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Isometric Projections & views #2.pptx has 18 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Isometric Projections & views #3.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Isometric Projections & views #3.pptx has 47 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Engineering Graphics/Notes-Projection of Points & Lines.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Py

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LINEAR ALGEBRA AND CALCULUS/Module 1 Course Handout Linear Algebra and Calculus.pdf has 51 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LINEAR ALGEBRA AND CALCULUS/Module II Course Handout MAT 101 Linear Algebra and Calculus.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LINEAR ALGEBRA AND CALCULUS/Module II Course Handout MAT 101 Linear Algebra and Calculus.pdf has 23 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LINEAR ALGEBRA AND CALCULUS/Notes on 31-1-22 Telescopic sum.pdf
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LINEAR ALGEBRA AND CALCULUS/Notes on 31-1-22 Telescopic sum.pdf has 5 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/LIN

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Electrical & Electronics Engineering/PAS, Amplifier, Instrumentation.pptx has 58 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Electrical & Electronics Engineering/Rectifiers, Filters, Regulators.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Electrical & Electronics Engineering/Rectifiers, Filters, Regulators.pptx has 54 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Electrical & Electronics Engineering/Superheterodyne receiver.pptx
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/Basics of Electrical & Electronics Engineering/Superheterodyne receiver.pptx has 10 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files

In [36]:
len(all_parsed_docs)

13420

In [40]:
all_parsed_docs[2015]

Document(id_='507a8d33-e789-4ba9-b937-96844737b060', embedding=None, metadata={'module': 'Module5(4)', 'course': 'MANAGEMENT FOR SOFTWARE ENGINEERS', 'semester': 5, 'announcement': 'MODULE-5', 'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/data/MANAGEMENT FOR SOFTWARE ENGINEERS/3. Software quality .pptx', 'file_name': '3. Software quality .pptx', 'file_type': 'application/vnd.openxmlformats-officedocument.presentationml.presentation', 'file_size': 1444474, 'creation_date': '2024-10-20', 'last_modified_date': '2024-10-20', 'page_number': 10}, excluded_embed_metadata_keys=['file_path', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'page_number', 'file_name', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'last_accessed_date'], excluded_llm_metadata_keys=['file_path', 'file_type', 'file_size', 'creation_date', 'last_modified_date', 'page_number', 'file_name', 'file_type', 'file_size', 'creation_date', 'l

### ii) school data

In [74]:
""" Without image embeddings
"""

class CustomDocReader(BaseReader):
    def __init__(self, file_type, *args, **kwargs) :
        super().__init__(*args, **kwargs)
        
        self.file_type = file_type
        self.doc_parser = self.find_doc_parser(file_type)
        
    
    def find_doc_parser(self, file_type) :
        if file_type == ".pdf" :
            return partition_pdf
        
        elif file_type == ".ppt" :
            return partition_ppt
        
        elif file_type == ".pptx" :
            return partition_pptx
        
        elif file_type == ".doc" :
            return partition_doc
        
        elif file_type == ".docx" :
            return partition_docx
        
        
    def format_text(self, type_, doc_text) :
        text = ""
        
        if type_ == "Title" :
            text = doc_text + "\n"
        elif type_ in ["Footer", "PageNumber"] :
            pass
        elif type_ == "ListItem" :
            text = "  -" + doc_text + "\n"
        elif type_ in ["Formula", "Table"] :
            text = "\n" + doc_text + "\n\n"
        else :
            text = doc_text + "\n"
        
        return text
        
    
    def load_data(self, file, extra_info=dict()):
        print(f"file: {file}")
        elements = partition_pdf(file, languages=["eng"])
        # load_data returns a list of Document objects
        docs = list()
        text = ""
        extra_info = dict()
        prev_pg_no = elements[0].metadata.page_number

        doc_info = search_docs_by_keys(
            documents_info,
            {
                "subject": elements[0].metadata.file_directory.split("/")[-1],
                "file_name": elements[0].metadata.filename
            }
        )
        extra_info["chapter"] = doc_info[0]["chapter"]
        extra_info["subject"] = doc_info[0]["subject"]
        extra_info["grade"] = doc_info[0]["grade"]
        extra_info["post_title"] = doc_info[0]["type"]["post_title"]
        extra_info["post_description"] = doc_info[0]["type"]["post_description"]
        extra_info["course_info"] = doc_info[0]["course_info"]

        # Add file metadata
        file_metadata = default_file_metadata_func(file)
        for meta in file_metadata :
            if meta == "file_path" :
                extra_info[meta] = file_metadata[meta].as_posix()
            else :
                extra_info[meta] = file_metadata[meta]

        for element in elements:
            element_dict = element.to_dict()

            if element.metadata.page_number == prev_pg_no :
                # Format data and add to text
                text += format_text(element_dict["type"], element_dict["text"])
            else :
                extra_info["page_number"] = prev_pg_no
                docs.append(
                    Document(
                        text = text,
                        metadata=extra_info.copy(),
                        excluded_embed_metadata_keys=[
                            "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                        excluded_llm_metadata_keys=[
                            "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                    )
                )

                text = ""
                text += format_text(element_dict["type"], element_dict["text"])
            prev_pg_no = element.metadata.page_number

        else :
            extra_info["page_number"] = prev_pg_no
            docs.append(
                Document(
                    text = text,
                    metadata=extra_info.copy(),
                    excluded_embed_metadata_keys=[
                        "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                    ],
                    excluded_llm_metadata_keys=[
                        "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                    ],
                )
            )
            
        print(f"file: {file} has {len(docs)} pages\n")
        return docs

In [27]:
""" With image embeddings
"""
class CustomDocReader(BaseReader):
    def __init__(self, file_type, *args, **kwargs) :
        super().__init__(*args, **kwargs)
        
        self.file_type = file_type
        self.doc_parser = self.find_doc_parser(file_type)
        self.img_dir = None
        
    
    def find_doc_parser(self, file_type) :
        if file_type == ".pdf" :
            return partition_pdf
        
        elif file_type == ".ppt" :
            return partition_ppt
        
        elif file_type == ".pptx" :
            return partition_pptx
        
        elif file_type == ".doc" :
            return partition_doc
        
        elif file_type == ".docx" :
            return partition_docx
        
        
    def format_text(self, element_dict) :
        type_ = element_dict["type"]
        doc_text = element_dict["text"]
        text = ""

        if type_ == "Title" :
            text = doc_text + "\n"
        elif type_ in ["Footer", "PageNumber"] :
            pass
        elif type_ == "ListItem" :
            text = "  -" + doc_text + "\n"
        elif type_ in ["Formula", "Table"] :
            text = "\n" + doc_text + "\n\n"
        else :
            text = doc_text + "\n"

        return text
    
    def filter_valid_images(self, elements) :
        valid_imgs = list()
        for element in elements :
            element_dict = element.to_dict()
            if element_dict["type"] == "Image" and len(element_dict["text"].split(" "))<=3 :
                valid_imgs.append(element_dict["metadata"]["image_path"])
        valid_imgs = [os.path.abspath(img) for img in valid_imgs]

        return valid_imgs
    
    
    def check_and_delete_image(self, images, figs, max_aspect_ratio=100):
        """ Remove all image files that have not been identified as true images
        """   
        valid_imgs = list()
        for fig in figs :
            fig_path = os.path.abspath(os.path.join(self.img_dir, fig))
            # Open the image and get its dimensions
            with Image.open(fig_path) as img:
                width, height = img.size

                # Calculate the aspect ratio
                aspect_ratio = width / height if width > height else height / width

                # Check if the aspect ratio exceeds the maximum allowed
                if aspect_ratio > max_aspect_ratio or fig_path not in images or width < 10 or height < 10 :
                    os.remove(fig_path)
                else :
                    valid_imgs.append(fig_path)
        return valid_imgs
        
    
    def load_data(self, file, extra_info=dict()):
        print(f"file: {file}")
        IMAGES = list()
        self.img_dir = f"./Static/{uuid.uuid4()}/figures/"

        try :
            elements = partition_pdf(
                file,
                languages=["eng"],
                extract_image_block_types=["Image"],
                extract_image_block_output_dir=self.img_dir
            )
        except Exception as e :
            elements = partition_pdf(
                file,
                languages=["eng"],
            )
        
        # Remove all extra unwanted images
        valid_imgs = self.filter_valid_images(elements)
        figs = os.listdir(self.img_dir)
        valid_imgs = self.check_and_delete_image(valid_imgs, figs)
        print(f"{len(valid_imgs)} valid images")

        # load_data returns a list of Document objects
        docs = list()
        text = ""
        extra_info = dict()
        prev_pg_no = elements[0].metadata.page_number

        doc_info = search_docs_by_keys(
            documents_info,
            {
                "subject": elements[0].metadata.file_directory.split("/")[-1],
                "file_name": elements[0].metadata.filename
            }
        )
        extra_info["chapter"] = doc_info[0]["chapter"]
        extra_info["subject"] = doc_info[0]["subject"]
        extra_info["grade"] = doc_info[0]["grade"]
        extra_info["post_title"] = doc_info[0]["type"]["post_title"]
        extra_info["post_description"] = doc_info[0]["type"]["post_description"]
        extra_info["course_info"] = doc_info[0]["course_info"]

        # Add file metadata
        file_metadata = default_file_metadata_func(file)
        for meta in file_metadata :
            if meta == "file_path" and isinstance(file_metadata[meta], PosixPath) :
                extra_info[meta] = file_metadata[meta].as_posix()
            else :
                extra_info[meta] = file_metadata[meta]

        for element in elements:
            element_dict = element.to_dict()
            # If the element is a true image, add it as a separate document
            if element_dict["type"] == "Image" and os.path.abspath(element_dict["metadata"]["image_path"]) in valid_imgs :
                img_str = image_to_base64(element_dict["metadata"]["image_path"])
                img_summary = get_multimodal_response(groq_client, img_str).content

                # Add additional metadata
                img_metadata = extra_info.copy()
                img_metadata["page_number"] = element_dict["metadata"]["page_number"]
                img_metadata["doc_type"] = "Image"
                img_metadata["image_path"] = element_dict["metadata"]["image_path"]

                docs.append(
                    Document(
                        text = img_summary,
                        metadata=img_metadata,
                        excluded_embed_metadata_keys=[
                            "image_path", "doc_type", "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                        excluded_llm_metadata_keys=[
                            "image_path", "doc_type", "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number"
                        ],
                    )
                )


            elif element.metadata.page_number == prev_pg_no :
                # Format data and add to text
                text += self.format_text(element_dict)
            else :
                extra_info["page_number"] = prev_pg_no
                extra_info["doc_type"] = "Text"
                docs.append(
                    Document(
                        text = text,
                        metadata=extra_info.copy(),
                        excluded_embed_metadata_keys=[
                            "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number", "image_path"
                        ],
                        excluded_llm_metadata_keys=[
                            "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number", "image_path"
                        ],
                    )
                )

                text = ""
                text += self.format_text(element_dict)
            prev_pg_no = element.metadata.page_number

        else :
            extra_info["page_number"] = prev_pg_no
            extra_info["doc_type"] = "Text"
            docs.append(
                Document(
                    text = text,
                    metadata=extra_info.copy(),
                    excluded_embed_metadata_keys=[
                        "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number", "image_path"
                    ],
                    excluded_llm_metadata_keys=[
                        "file_path", "file_name", "file_type", "file_size", "creation_date", "last_modified_date", "page_number", "image_path"
                    ],
                )
            )
            
        print(f"file: {file} has {len(docs)} pages\n")
        return docs

In [40]:
# To test ou the parsing method
test_parsed_docs = SimpleDirectoryReader(
    input_files=["./8_grade_texts/mathematics/hemh101.pdf"],
    file_extractor={
        ".pdf": CustomDocReader(".pdf"),
        ".doc": CustomDocReader(".doc"),
        ".ppt": CustomDocReader(".ppt"),
        ".docx": CustomDocReader(".docx"),
        ".pptx": CustomDocReader(".pptx"),
    },
    recursive=True
).load_data()

file: 8_grade_texts/mathematics/hemh101.pdf
13 valid images
file: 8_grade_texts/mathematics/hemh101.pdf has 25 pages



In [42]:
for doc in test_parsed_docs :
    if doc.metadata["doc_type"] == "Text" :
        print("*"*100)
        print(doc.text)
        print("\n\n")

****************************************************************************************************
RATIONAL NUMBERS    1  CHAPTER1  Rational  Numbers  1.1    Introduction  In Mathematics, we frequently come across simple equations to be solved. For example,  x + 2 = 13  the equation  (1)  is solved when x = 11, because this value of x satisfies the given equation. The  solution  11 is a natural number. On the other hand, for the equation  x + 5 = 5  (2)  the solution gives the whole number 0 (zero). If we consider only natural numbers,  equation (2) cannot be solved. To solve equations like (2), we added the number zero to  the collection of natural numbers and obtained the whole numbers. Even whole numbers  will not be sufficient to solve equations of type  x + 18 = 5  (3)  Do you see ‘why’? We require the number –13 which is not a whole number. This  led us to think of integers, (positive and negative). Note that the positive integers  correspond to natural numbers. One may think t

In [28]:
""" Go course by course, parse through the documents within and add to the set of all
parsed documents
"""
courses = os.listdir("8_grade_texts")
all_parsed_docs = list()
course_count = 0

for course in courses :
    course_count += 1
    print("*"*100)
    print(f"Course: {course}")
    
    start_time = time.time()
    cparsed_docs = SimpleDirectoryReader(
        input_dir=os.path.join("./8_grade_texts", course),
        file_extractor={
            ".pdf": CustomDocReader(".pdf"),
            ".doc": CustomDocReader(".doc"),
            ".ppt": CustomDocReader(".ppt"),
            ".docx": CustomDocReader(".docx"),
            ".pptx": CustomDocReader(".pptx"),
        },
        recursive=True
    ).load_data()
    end_time = time.time()
    
    all_parsed_docs.extend(cparsed_docs)
    
    print(f"Total time taken for execution was {(end_time - start_time)}sec")
    print(f"{course_count} courses done!")
    
    print("Sleeping for 1 sec..😴\n\n")
    time.sleep(1)

****************************************************************************************************
Course: mathematics
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf
13 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf has 25 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh102.pdf
3 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh102.pdf has 7 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh103.pdf
12 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh103.pdf has 28 pages

file: /home/jovanzac/Jovan/OfflineP

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

...

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

Failed to load file /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh113.pdf with error: 'image_path'. Skipping...
Total time taken for execution was 958.4045004844666sec
1 courses done!
Sleeping for 1 sec..😴


****************************************************************************************************
Course: English
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd101.pdf
32 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd101.pdf has 40 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd102.pdf
30 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd102.pdf has 39 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_lea

Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 217, in save_elements
    write_image(cropped_image, output_f_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_utils.py", line 48, in write_image
    image.save(output_image_path)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/Image.py", line 2568, in save
    save_handler(self, fp, filename)
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/PIL/JpegImagePlugin.py", line 636, in _save
    raise ValueError(msg)
ValueError: cannot write empty image as JPEG
Image Extraction Error: Skipping the failed image
Traceback (most recent call last):
  File "/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/unstructured/partition/pdf_image/pdf_image_ut

Failed to load file /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd108.pdf with error: 'image_path'. Skipping...
Total time taken for execution was 671.0985045433044sec
2 courses done!
Sleeping for 1 sec..😴


****************************************************************************************************
Course: Science
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Science/gesc101.pdf
27 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Science/gesc101.pdf has 35 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Science/gesc102.pdf
23 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Science/gesc102.pdf has 33 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learnin

14 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess205.pdf has 27 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess206.pdf
12 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess206.pdf has 23 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess207.pdf
20 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess207.pdf has 34 pages

file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/History_(Social_Science)/hess208.pdf
23 valid images
file: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_le

In [41]:
""" If file_path is of type POSIX, converts to str
"""
def is_posix_path(path) :
    return isinstance(path, PosixPath)

for doc in all_parsed_docs :
    doc_dict = doc.to_dict()
    if is_posix_path(doc_dict["metadata"]["file_path"]) :
        print(doc.metadata)
        doc.metadata["file_path"] = doc.metadata["file_path"].as_posix()

NameError: name 'all_parsed_docs' is not defined

In [16]:
len(all_parsed_docs)

1621

In [17]:
all_parsed_docs[0].to_dict()["metadata"]["page_number"]

1

In [131]:
""" Checks to any documents are missing page numbers. Should print nothing
"""
mcounter = 0
counter= 0
invalid_indices = []

for i, doc in enumerate(proofred_docs) :
    doc = doc.to_dict()
    if "page_number" not in doc["metadata"] :
        print("*"*50+"\n\n")
        print(f"file_type: {doc['metadata']['file_type']}; file_path: {doc['metadata']['file_path']}")
        counter += 1
        invalid_indices.append(i)
        
    mcounter += 1

In [132]:
print(counter)
print(mcounter)
print(invalid_indices)

0
1621
[]


In [28]:
""" TO Proof read and correct the texts
"""
def wfw_template_str(pg_text) :
    wfw_tmpl_str = f"""\
    ## INSTRUCTIONS
    Your task is to proofread and improve the text in the section titled **TEXT**, adhering to the rules below:
    
    ### TASK REQUIREMENTS
    1. Ensure the text is **grammatically and structurally correct**. 
    2. Make **minimal edits** to fix:
       - Grammatical errors.
       - Structural inconsistencies.
       - Unnecessary words that distort meaning.
    3. Maintain the **original meaning and intent** of the text.

    ### RULES
    - DO NOT rewrite or paraphrase unless required to fix errors.
    - DO NOT generate any additional commentary or output beyond the corrected text.
    - Provide the corrected text **exactly as specified** in the output format.
    - Return the text with corrections directly, adhering to the task requirements and rules
    - DO NOT include any additional formatting or annotations.
    - DO NOT generate any additional sentences or words in the response.

    ## TEXT
    {pg_text}

    ## OUTPUT FORMAT
    <The corrected text>
    """

    
    return wfw_tmpl_str

In [84]:
def clean_text(llm, text) :
    tmpl_str = wfw_template_str(text)
    llm_res = llm.complete(tmpl_str).text
    output_string = re.sub(r"Here is the corrected text:", "", llm_res, re.IGNORECASE).strip()
    
    return output_string

In [29]:
proofred_docs = copy.deepcopy(all_parsed_docs)
len(proofred_docs)

1621

In [31]:
""" Replace text field of each node with text proofread and corrected by an llm
"""
llm_count = 0
llm = llms[llm_count]

for i, doc in enumerate(proofred_docs) :
    if doc.metadata["doc_type"] == "Text" :
        print(f"i: {i}")
        try :
            llm_res = clean_text(llm, doc.text.strip())

            doc.text = llm_res
        except Exception as exp :
            if llm_count != 2 :
                llm_count += 1
            else :
                print(f"Last document index: {i}")
                raise exp
            llm = llms[llm_count]

i: 2
i: 4
i: 6
i: 8
i: 10
i: 12
i: 14
i: 16
i: 19
i: 21
i: 23
i: 24
i: 26
i: 28
i: 30
i: 31
i: 32
i: 33
i: 34
i: 37
i: 38
i: 40
i: 41
i: 44


Retrying llama_index.llms.openai.base.OpenAI._chat in 0.6559774833426967 seconds as it raised InternalServerError: Error code: 503 - {'error': {'message': 'Service Unavailable', 'type': 'internal_server_error'}}.


i: 45
i: 48
i: 49
i: 51
i: 53
i: 54
i: 57
i: 59
i: 74
i: 76
i: 77
i: 78
i: 79
i: 80
i: 83
i: 85
i: 87
i: 89
i: 93
i: 96
i: 97
i: 100
i: 104
i: 106
i: 109
i: 110
i: 112
i: 114
i: 116
i: 118
i: 120
i: 122
i: 123
i: 124
i: 126
i: 128
i: 129
i: 131
i: 132
i: 134
i: 136
i: 137
i: 140
i: 142
i: 144
i: 146
i: 147
i: 149
i: 151
i: 153
i: 155
i: 157
i: 163


Retrying llama_index.llms.openai.base.OpenAI._chat in 0.4545707471985615 seconds as it raised InternalServerError: Error code: 503 - {'error': {'message': 'Service Unavailable', 'type': 'internal_server_error'}}.


i: 168
i: 170
i: 171
i: 172
i: 174
i: 178
i: 180
i: 182
i: 183
i: 185
i: 187
i: 190
i: 191
i: 193
i: 194
i: 196
i: 198
i: 199
i: 200
i: 205
i: 206
i: 208
i: 210
i: 213
i: 216
i: 220
i: 223
i: 224
i: 227
i: 231
i: 232
i: 234
i: 236
i: 239
i: 241
i: 243
i: 245
i: 246
i: 247
i: 249
i: 252
i: 254
i: 257
i: 260
i: 263
i: 265
i: 269
i: 274
i: 276
i: 277
i: 280
i: 283
i: 287
i: 289
i: 291
i: 292
i: 293
i: 295
i: 296


Retrying llama_index.llms.openai.base.OpenAI._chat in 0.33559177686957886 seconds as it raised InternalServerError: Error code: 503 - {'error': {'message': 'Service Unavailable', 'type': 'internal_server_error'}}.


i: 297
i: 299
i: 300
i: 302
i: 303
i: 306
i: 312
i: 316
i: 322
i: 328
i: 334
i: 338
i: 343
i: 348
i: 353
i: 359
i: 363
i: 368
i: 373
i: 376
i: 378
i: 382
i: 390
i: 392
i: 394
i: 396
i: 399
i: 401
i: 404
i: 405
i: 408
i: 411
i: 417
i: 426
i: 432
i: 438
i: 444
i: 450
i: 455
i: 460
i: 465
i: 470
i: 475
i: 480
i: 484
i: 486
i: 494
i: 499
i: 506
i: 512
i: 516
i: 519
i: 522
i: 532
i: 537
i: 542
i: 547
i: 551
i: 556
i: 561
i: 564
i: 570
i: 576
i: 582
i: 587
i: 592
i: 595
i: 599
i: 610
i: 612
i: 617
i: 623
i: 626
i: 627
i: 629
i: 631
i: 637
i: 643
i: 647
i: 649
i: 650
i: 658
i: 659
i: 660
i: 662
i: 665
i: 668
i: 670


Retrying llama_index.llms.openai.base.OpenAI._chat in 0.11467525725916139 seconds as it raised RateLimitError: Error code: 429 - {'error': {'message': 'Rate limit reached for model `llama3-70b-8192` in organization `org_01hx7j0ccyedcv123fcyhabqj4` on : Limit 500000, Used 499280, Requested 1109. Please try again in 1m7.092s. Visit https://console.groq.com/docs/rate-limits for more information.', 'type': '', 'code': 'rate_limit_exceeded'}}.
Retrying llama_index.llms.openai.base.OpenAI._chat in 0.2539431893319395 seconds as it raised RateLimitError: Error code: 429 - {'error': {'message': 'Rate limit reached for model `llama3-70b-8192` in organization `org_01hx7j0ccyedcv123fcyhabqj4` on : Limit 500000, Used 499277, Requested 1109. Please try again in 1m6.661999999s. Visit https://console.groq.com/docs/rate-limits for more information.', 'type': '', 'code': 'rate_limit_exceeded'}}.


i: 674
i: 678
i: 680
i: 682
i: 685
i: 687
i: 689
i: 695
i: 698
i: 700
i: 703
i: 704
i: 705
i: 706
i: 709
i: 712
i: 714
i: 717
i: 718
i: 721
i: 724
i: 725
i: 727
i: 729
i: 732
i: 734
i: 736
i: 737
i: 740
i: 744
i: 748
i: 749
i: 753
i: 755
i: 762
i: 765
i: 768
i: 769
i: 772
i: 790
i: 795
i: 796
i: 799
i: 802
i: 805
i: 806
i: 810
i: 814
i: 820
i: 822
i: 825
i: 829
i: 830
i: 831
i: 833
i: 837
i: 839
i: 842
i: 844
i: 845
i: 846
i: 847
i: 850
i: 861
i: 865
i: 868
i: 872
i: 875
i: 878
i: 881
i: 882
i: 884
i: 890
i: 892
i: 896
i: 900
i: 904
i: 907
i: 911
i: 915
i: 920
i: 922
i: 925
i: 930
i: 936
i: 940
i: 941
i: 943
i: 946
i: 951
i: 954
i: 957
i: 960
i: 962
i: 966
i: 967
i: 969
i: 976
i: 978
i: 979
i: 980
i: 984
i: 988
i: 992
i: 994
i: 995
i: 998
i: 1001
i: 1003
i: 1006
i: 1008
i: 1009
i: 1011
i: 1013
i: 1017
i: 1018
i: 1020
i: 1021
i: 1025
i: 1035
i: 1037
i: 1039
i: 1041
i: 1043
i: 1046
i: 1048
i: 1049
i: 1051
i: 1052
i: 1055
i: 1057
i: 1058
i: 1059
i: 1062
i: 1063
i: 1064
i: 1067
i: 1068
i: 

In [78]:
""" Fix the text for the pages with blank text (Generally not required)
"""
wrong_text = [1483, 299, 297, 277, 269, 234, 216, 193, 187, 183, 178, 153, 140, 112, 28]

for i in wrong_text :
    text = all_parsed_docs[i].text
    llm_res = clean_text(groq_text_llm3, text)
    proofred_docs[i].text = llm_res
    print(f"i: {i}")
    print(proofred_docs[i].text)
    print("*"*100 + "\n\n")

i: 1483
Here is the corrected text:

Humans use huge amounts of water not only for drinking and washing but also in the process of production. Water for agriculture, industries, and generating electricity through reservoirs of activity dams are the other usages. An average urban Indian uses about 150 litres of water every day.

Use:
Litres per person per day
Drinking: 3
Cooking: 4
Bathing: 20
Flushing: 40
Washing clothes: 40
Washing utensils: 20
Gardening: 23
Total: 150
Can you suggest some ways to bring down this amount?

Problems of Water availability:
There is scarcity of water in many regions of the world. Most of Africa, West Asia, South Asia, parts of western USA, north-west Mexico, parts of South America, and entire Australia are facing shortages in fresh water supply. Countries located in climatic zones most susceptible to droughts face great problems of water scarcity. Thus, water shortage may be a consequence of variation in seasonal or annual precipitation or the scarcity is

i: 269
Here is the corrected text:

Since the speed is uniform, the distance covered would be directly proportional to time. 

x = 75 × 20 / 60 = 25, so the train will cover a distance of 25 km in 20 minutes.

Also, y = 250 × 60 / 75 = 200 minutes or 3 hours 20 minutes. Therefore, 3 hours 20 minutes will be required to cover a distance of 250 kilometers.

Alternatively, when x is known, then one can determine y from the relation.

You know that a map is a miniature representation of a very large region. A scale is usually given at the bottom of the map. The scale shows a relationship between actual length and the length represented on the map. The scale of the map is thus the ratio of the distance between two points on the map to the actual distance between two points on the large region.

For example, if 1 cm on the map represents 8 km of actual distance [i.e., the scale is 1 cm : 8 km or 1 : 800,000], then 2 cm on the same map will represent 16 km. Hence, we can say that the scale of

i: 183

****************************************************************************************************


i: 178
Here is the corrected text:

Aruna asked what is to be done if there is a decrease. The teacher then considered the following example. 

Example 10: A TV was bought at a price of Rs. 21,000. After one year, the value of the TV was depreciated by 5% (Depreciation means reduction of value due to use and age of the item). Find the value of the TV after one year.

Solution: 
Principal = Rs. 21,000 
Reduction = 5% of Rs. 21,000 per year 
= (21,000 × 5) / 100 
= Rs. 1,050 
value at the end of 1 year = Rs. 21,000 – Rs. 1,050 = Rs. 19,950 

Alternately, we may directly get this as follows: 
value at the end of 1 year = Rs. 21,000 × (1 - 5/100) 
= Rs. 21,000 × 19/20 
= Rs. 19,950 

TRY THESE: 
1. A machinery worth Rs. 10,500 depreciated by 5%. Find its value after one year. 
2. Find the population of a city after 2 years, which is at present 12 lakh, if the rate of increase is 4

In [85]:
"""Removing the extra text added by the llm
"""
for i, doc in enumerate(proofred_docs) :
    output_string = re.sub(r"Here is the corrected text:", "", doc.text, re.IGNORECASE).strip()
    doc.text = output_string
    print(f"i: {i}")
    print(doc.text)
    print("*"*100)

i: 0
The image displays a bar code or QR code that has a pattern of white and dark bars on it. This type of code is used to track contents of bags. The bars create a sense of depth and highlights in the design of the barcode. The pattern of bars make it unique and interesting to look at, resembling a pair of scissors, and can appear like a letter or image.
****************************************************************************************************
i: 1
A man and a woman are sitting at a table next to each other, engrossed in a book. They seem to be having a good conversation, possibly about a newspaper article or other related topic. The woman appears to be pointing at something in the book, and they both seem relaxed and enjoying the interaction. The atmosphere appears to be warm and friendly, as they cooperate and share their thoughts on a particular subject.
****************************************************************************************************
i: 2
RATIONAL NUM

In [87]:
for doc in proofred_docs :
    if doc.metadata["doc_type"] == "Text" :
        print("*"*100)
        print(doc.text)
        print("\n\n")

****************************************************************************************************
RATIONAL NUMBERS

CHAPTER 1

1.1 Introduction

In Mathematics, we frequently come across simple equations to be solved. For example, x + 2 = 13; the equation (1) is solved when x = 11, because this value of x satisfies the given equation. The solution 11 is a natural number. On the other hand, for the equation x + 5 = 5 (2), the solution gives the whole number 0 (zero). If we consider only natural numbers, equation (2) cannot be solved. To solve equations like (2), we added the number zero to the collection of natural numbers and obtained the whole numbers. Even whole numbers will not be sufficient to solve equations of type x + 18 = 5 (3). Do you see why? We require the number –13, which is not a whole number. This led us to think of integers (positive and negative). Note that the positive integers correspond to natural numbers. One may think that we have enough numbers to solve all si

In [89]:
for doc in proofred_docs[:50] :
    if doc.metadata["doc_type"] == "Image" :
        print("*"*100)
        print(doc.text)
        print("\n\n")

****************************************************************************************************
The image displays a bar code or QR code that has a pattern of white and dark bars on it. This type of code is used to track contents of bags. The bars create a sense of depth and highlights in the design of the barcode. The pattern of bars make it unique and interesting to look at, resembling a pair of scissors, and can appear like a letter or image.



****************************************************************************************************
A man and a woman are sitting at a table next to each other, engrossed in a book. They seem to be having a good conversation, possibly about a newspaper article or other related topic. The woman appears to be pointing at something in the book, and they both seem relaxed and enjoying the interaction. The atmosphere appears to be warm and friendly, as they cooperate and share their thoughts on a particular subject.



*********************

In [90]:
""" Just printing all text documents.
"""
for i, doc in enumerate(proofred_docs) :
    doc = doc.to_dict()
    if doc["metadata"]["doc_type"] == "Text" :
        print("*"*100)
        print(f"No: {i}; file_type: {doc['metadata']['file_type']}; file_path: {doc['metadata']['file_path']}")
        print("\n")
        display(doc)
        print("\n\n")

****************************************************************************************************
No: 2; file_type: application/pdf; file_path: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf




{'id_': '57c23a18-0cdb-4a28-ba22-3e577fd4fdd3',
 'embedding': None,
 'metadata': {'chapter': 'Chapter1',
  'subject': 'Mathematics',
  'grade': '8th Standard',
  'post_title': 'Chapter 1',
  'post_description': 'The notes for chapter 1 has been uploaded',
  'course_info': '8th Standard Mathematics',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf',
  'file_name': 'hemh101.pdf',
  'file_type': 'application/pdf',
  'file_size': 1233342,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 1,
  'doc_type': 'Text'},
 'excluded_embed_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'image_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'last_accessed_date'],
 'excluded_llm_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  '




****************************************************************************************************
No: 4; file_type: application/pdf; file_path: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf




{'id_': '3e388f0b-dec1-4ee4-9f40-729a3c99a350',
 'embedding': None,
 'metadata': {'chapter': 'Chapter1',
  'subject': 'Mathematics',
  'grade': '8th Standard',
  'post_title': 'Chapter 1',
  'post_description': 'The notes for chapter 1 has been uploaded',
  'course_info': '8th Standard Mathematics',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf',
  'file_name': 'hemh101.pdf',
  'file_type': 'application/pdf',
  'file_size': 1233342,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 2,
  'doc_type': 'Text'},
 'excluded_embed_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'image_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'last_accessed_date'],
 'excluded_llm_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  '




****************************************************************************************************
No: 6; file_type: application/pdf; file_path: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf




...

{'id_': 'd7232b76-93a1-492d-bbf4-b74beaa7dc2d',
 'embedding': None,
 'metadata': {'chapter': 'Chapter5',
  'subject': 'Geography_(Social_Science)',
  'grade': '8th Standard',
  'post_title': 'Chapter 5',
  'post_description': 'The notes for chapter 5 has been uploaded',
  'course_info': '8th Standard Geography (Social Science)',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Geography_(Social_Science)/hess405.pdf',
  'file_name': 'hess405.pdf',
  'file_type': 'application/pdf',
  'file_size': 1779988,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 6,
  'doc_type': 'Text'},
 'excluded_embed_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'image_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'last_accessed_date'],
 'excluded_llm_metadata_keys': ['




****************************************************************************************************
No: 1617; file_type: application/pdf; file_path: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Geography_(Social_Science)/hess405.pdf




{'id_': '65b67c1a-8b79-427f-bfe3-a0cef4f909ac',
 'embedding': None,
 'metadata': {'chapter': 'Chapter5',
  'subject': 'Geography_(Social_Science)',
  'grade': '8th Standard',
  'post_title': 'Chapter 5',
  'post_description': 'The notes for chapter 5 has been uploaded',
  'course_info': '8th Standard Geography (Social Science)',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Geography_(Social_Science)/hess405.pdf',
  'file_name': 'hess405.pdf',
  'file_type': 'application/pdf',
  'file_size': 1779988,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 7,
  'doc_type': 'Text'},
 'excluded_embed_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'image_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'last_accessed_date'],
 'excluded_llm_metadata_keys': ['




****************************************************************************************************
No: 1620; file_type: application/pdf; file_path: /home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Geography_(Social_Science)/hess405.pdf




{'id_': '354ccac3-c3c8-445e-8f5a-a25e8dc5a6ec',
 'embedding': None,
 'metadata': {'chapter': 'Chapter5',
  'subject': 'Geography_(Social_Science)',
  'grade': '8th Standard',
  'post_title': 'Chapter 5',
  'post_description': 'The notes for chapter 5 has been uploaded',
  'course_info': '8th Standard Geography (Social Science)',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/Geography_(Social_Science)/hess405.pdf',
  'file_name': 'hess405.pdf',
  'file_type': 'application/pdf',
  'file_size': 1779988,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 8,
  'doc_type': 'Text'},
 'excluded_embed_metadata_keys': ['file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'image_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'last_accessed_date'],
 'excluded_llm_metadata_keys': ['

## 4) Serialize all parsed documents

In [91]:
# with open(f"data_interm_storage/{SRC_TYPE}/proofread_docs.pkl", "wb") as pfile :
#     pickle.dump(proofred_docs, pfile)

In [93]:
# """ Serialze all the parsed docs
# """
# with open(f"data_interm_storage/{SRC_TYPE}/docs_parsed.pkl", "wb") as pfile :
#     pickle.dump(all_parsed_docs, pfile)

In [17]:
with open(f"data_interm_storage/{SRC_TYPE}/proofread_docs.pkl", "rb") as pfile :
    docs_parsed = pickle.load(pfile)

In [37]:
# with open(f"data_interm_storage/{SRC_TYPE}/docs_parsed.pkl", "rb") as pfile :
#     docs_parsed = pickle.load(pfile)

In [18]:
print(len(docs_parsed))
docs_parsed[2].text

1621


'RATIONAL NUMBERS\n\nCHAPTER 1\n\n1.1 Introduction\n\nIn Mathematics, we frequently come across simple equations to be solved. For example, x + 2 = 13; the equation (1) is solved when x = 11, because this value of x satisfies the given equation. The solution 11 is a natural number. On the other hand, for the equation x + 5 = 5 (2), the solution gives the whole number 0 (zero). If we consider only natural numbers, equation (2) cannot be solved. To solve equations like (2), we added the number zero to the collection of natural numbers and obtained the whole numbers. Even whole numbers will not be sufficient to solve equations of type x + 18 = 5 (3). Do you see why? We require the number –13, which is not a whole number. This led us to think of integers (positive and negative). Note that the positive integers correspond to natural numbers. One may think that we have enough numbers to solve all simple equations with the available list of integers. Now consider the equations 2x = 3 (4) and 

# IV) Creating the data stores

In [126]:
docs_parsed_copy = copy.deepcopy(docs_parsed)

In [127]:
""" Consolidating all pagewise documents into single document ones
"""
docs_by_path = dict()
for doc in docs_parsed_copy :
    file_path = doc.metadata["file_path"]
    if doc.metadata["doc_type"] != "Image" :
        if file_path not in docs_by_path :
            # Remove page_number from metadata
            doc.metadata.pop("page_number", None)
            docs_by_path[file_path] = doc
        else :
            docs_by_path[file_path].text += f"\n\n\n{doc.text}"
    else :
        pass

documents = list(docs_by_path.values())

In [128]:
# Note: Missing 2 documents because they failed to parse earlier with error "image_path"
len(documents)

53

## 1) Splitting into Nodes

### a) Semantic Double Merging Chunking (For BM25 Retriever)

In [100]:
""" Only for testing purposes. To test out different parameters
"""

def display_node_content(nodes) :
    n = 0
    while nodes[n].metadata["file_path"][-19:] != "Science/gesc108.pdf" :
        n += 1
    print(n)
    file = nodes[n].metadata["file_path"]
    while nodes[n].metadata["file_path"] == file :
        print("*" * 100)
        print(nodes[n].text)
        print("\n\n\n")
        n += 1

In [101]:
lang_config = LanguageConfig(language="english", spacy_model="en_core_web_md")

splitter = SemanticDoubleMergingSplitterNodeParser(
    language_config=lang_config,
    initial_threshold=0.6,
    appending_threshold=0.7,
    merging_threshold=0.6,
    max_chunk_size=5000,
    include_metadata=True,
    include_prev_next_rel=True
)

In [102]:
nodes = splitter.get_nodes_from_documents(documents)

/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/llama_index/core/node_parser/text/semantic_double_merging_splitter.py:228: UserWarning: [W008] Evaluating Doc.similarity based on empty vectors.
  ).similarity(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/llama_index/core/node_parser/text/semantic_double_merging_splitter.py:255: UserWarning: [W008] Evaluating Doc.similarity based on empty vectors.
  ).similarity(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/llama_index/core/node_parser/text/semantic_double_merging_splitter.py:297: UserWarning: [W008] Evaluating Doc.similarity based on empty vectors.
  current_nlp.similarity(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/llama_index/core/node_parser/text/semantic_double_merging_splitter.py:310: UserWarning: [W008] Evaluating Doc.similarity based on empty vectors.
  and current_nlp.similarity(
/home/jovanzac/anaconda3/envs/iris/lib/python3.10/site-packages/llama_index/

In [56]:
""" Tested out the following configs:
0.7, 0.5, 0.6
0.7, 0.8, 0.7
0.7, 0.6, 0.6
0.4, 0.5, 0.5
0.6, 0.7, 0.6

The one finally chosen was:
0.6, 0.7, 0.6
"""
display_node_content(nodes)

974
****************************************************************************************************
8  Reproduction in Plants  T o  produce   reproduction, new plants are obtained  its  kind   is  a  characteristic  of  all  living  from seeds.




****************************************************************************************************
organisms.




****************************************************************************************************
You  have  already  learnt this in Class VI.




****************************************************************************************************
The production  of new individuals from their parents is  Paheli thought that new  known  as  reproduction. But,  how  do  plants always grow from seeds. plants  reproduce? There  are  different  But, she has never seen the seeds  modes of reproduction in plants which  of sugarcane, potato and rose. She  we shall learn in this chapter. wants to know how these plants  8.1 MODES

### b) Hierarchial chunking (For auto merging retrieval)

In [133]:
h_node_parser = HierarchicalNodeParser.from_defaults(
    include_metadata=True,
    include_prev_next_rel=True
)

In [104]:
hierarchical_nodes = h_node_parser.get_nodes_from_documents(documents)
len(hierarchical_nodes)

5660

In [105]:
leaf_nodes = get_leaf_nodes(hierarchical_nodes)

### c) Converting documents (all docs including images) into nodes (For Word-for-word search)

In [106]:
print(len(docs_parsed))
docs_parsed[0].to_dict()

1621


{'id_': 'ee888fcc-d61d-42db-ad8d-f71532b2d4ed',
 'embedding': None,
 'metadata': {'chapter': 'Chapter1',
  'subject': 'Mathematics',
  'grade': '8th Standard',
  'post_title': 'Chapter 1',
  'post_description': 'The notes for chapter 1 has been uploaded',
  'course_info': '8th Standard Mathematics',
  'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf',
  'file_name': 'hemh101.pdf',
  'file_type': 'application/pdf',
  'file_size': 1233342,
  'creation_date': '2024-10-31',
  'last_modified_date': '2024-10-31',
  'page_number': 1,
  'doc_type': 'Image',
  'image_path': './Static/c5df1f9f-1957-493c-98ec-0f648bf96603/figures/figure-1-2.jpg'},
 'excluded_embed_metadata_keys': ['image_path',
  'doc_type',
  'file_path',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',
  'page_number',
  'file_name',
  'file_type',
  'file_size',
  'creation_date',
  'last_modified_date',


In [135]:
# Not required. Just to visualize doc_type and page numbers
img, text = 0, 0
for doc in docs_parsed :
    doc = doc.to_dict()
    print(doc)
    print(f"doc_type: {doc['metadata']['doc_type']};   page_number: {doc['metadata']['page_number']}")
    text += 1 if doc['metadata']['doc_type'] == "Text" else 0
    img += 1 if doc['metadata']['doc_type'] == "Image" else 0
print("*"*100)
print(text, img)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [171]:
# Rough code for reference
node1 = TextNode(text="<text_chunk>", id_="<node_1>")
node2 = TextNode(text="<text_chunk>", id_="<node_2>")
node3 = TextNode(text="<text_chunk>", id_="<node_3>")
node4 = TextNode(text="<text_chunk>", id_="<node_4>")

# set relationships
node1.relationships[NodeRelationship.NEXT] = RelatedNodeInfo(
    node_id=node2.node_id
)
node2.relationships[NodeRelationship.PREVIOUS] = RelatedNodeInfo(
    node_id=node1.node_id
)
node3.relationships[NodeRelationship.PARENT] = RelatedNodeInfo(
    node_id=node2.node_id
)
node4.relationships[NodeRelationship.PARENT] = RelatedNodeInfo(
    node_id=node2.node_id
)
node2.relationships[NodeRelationship.CHILD] = [
    RelatedNodeInfo(
        node_id=node3.node_id
    ),
    RelatedNodeInfo(
        node_id=node4.node_id
    ),
]

nodes = [node1, node2, node3, node4]

In [172]:
nodes[1].child_nodes

[RelatedNodeInfo(node_id='<node_3>', node_type=None, metadata={}, hash=None),
 RelatedNodeInfo(node_id='<node_4>', node_type=None, metadata={}, hash=None)]

In [136]:
""" Create hashmap with text docs as key and img docs on the same page as a list of values
"""
pg_to_docs = dict()

first_doc = docs_parsed[0].to_dict()
prev_pg = (first_doc["metadata"]["file_path"], first_doc["metadata"]["page_number"])
text_node, img_nodes = None, list()

for pg_doc in docs_parsed :
    doc = pg_doc.to_dict()
    doc_pg_id = (doc["metadata"]["file_path"], doc["metadata"]["page_number"])
    
    # When the page or document changes (To add values to the dict)
    if doc_pg_id != prev_pg :
        if not text_node :
            raise ValueError("Text node not set!!!")
        pg_to_docs[prev_pg] = [text_node, img_nodes]
        text_node, img_nodes = None, list()
    
    if doc["metadata"]["doc_type"] == "Text" :
        text_node = pg_doc
    elif doc["metadata"]["doc_type"] == "Image" :
        img_nodes.append(pg_doc)
        
    prev_pg = doc_pg_id

else :
    if not text_node :
        raise ValueError("Text node not set!!!")
    pg_to_docs[prev_pg] = [text_node, img_nodes]

In [137]:
# Just to visualize no of images per page
print(f"Total Number of pages accross all documents: {len(pg_to_docs)}\n\n")
for key in pg_to_docs :
    print(f"pg_identifier: {key};  no_imgs: {len(pg_to_docs[key][1])}\n\n")

Total Number of pages accross all documents: 564


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 1);  no_imgs: 2


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 2);  no_imgs: 1


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 3);  no_imgs: 1


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 4);  no_imgs: 1


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 5);  no_imgs: 1


pg_identifier: ('/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf', 6);  no_imgs: 1


pg_iden

In [138]:
""" Converting the docs in pg_to_docs to nodes
"""
pg_to_nodes = dict()
excluded_keys = [
    'image_path',
    'doc_type',
    'file_path',
    'file_name',
    'file_type',
    'file_size',
    'creation_date',
    'last_modified_date',
    'page_number',
    'file_name',
    'file_type',
    'file_size',
    'creation_date',
    'last_modified_date',
    'last_accessed_date'
]

for pg_id in pg_to_docs :
    # Getting the text and image node for this particular page
    text_doc, img_docs = pg_to_docs[pg_id]
    text_doc = text_doc.to_dict()
    
    # Initializing the text node
    text_node = TextNode(
        id_=text_doc["id_"],
        text=text_doc["text"],
        metadata=text_doc["metadata"],
        excluded_embed_metadata_keys=excluded_keys,
        excluded_llm_metadata_keys=excluded_keys,
    )
    
    img_nodes = list()
    for img_doc in img_docs :
        img_doc = img_doc.to_dict()
        
        img_node = ImageNode(
            id_=img_doc["id_"],
            text=img_doc["text"],
            image_path=img_doc["metadata"]["image_path"],
            metadata=img_doc["metadata"],
            excluded_embed_metadata_keys=excluded_keys,
            excluded_llm_metadata_keys=excluded_keys,
        )
        img_nodes.append(img_node)
    
    # Add the created nodes to pg_to_nodes hash
    pg_to_nodes[pg_id] = [text_node, img_nodes]

In [139]:
# Corresponds to no of pages
len(pg_to_nodes)

564

In [140]:
""" Setting Relationships for each node and creating the set of all nodes
Note: All text nodes are linked by prev-next relationships irrespective of which file they belong to.
All image nodes are only linked to their parent text node by parent-child relationship. They have no prev-next relationship
"""
all_nodes = list()

pg_ids = list(pg_to_nodes.keys())
prev_node, next_node = None, None
max_size = len(pg_ids)

for i, pg_id in enumerate(pg_ids) :
    cur_doc = pg_id[0]
    text_node, img_nodes = pg_to_nodes[pg_id]
    # Get the next node for the text node
    next_node = None if i==max_size-1 else pg_to_nodes[pg_ids[i+1]][0]
    
    # Set the node relationships for text_node
    if prev_node :
        text_node.relationships[NodeRelationship.PREVIOUS] = RelatedNodeInfo(
            node_id=prev_node.node_id,
            metadata=prev_node.metadata
        )
    if next_node :
        text_node.relationships[NodeRelationship.NEXT] = RelatedNodeInfo(
            node_id=next_node.node_id,
            metadata=next_node.metadata
        )
    
    # RNI- related node info
    img_rnis = list()
    for img_node in img_nodes :
        # Set te parent relatioship for each image node
        img_node.relationships[NodeRelationship.PARENT] = RelatedNodeInfo(
            node_id=text_node.node_id,
            metadata=text_node.metadata
        )
        
        img_rnis.append(
            RelatedNodeInfo(
                node_id=img_node.node_id,
                metadata=img_node.metadata
            )
        )
    
    # Set the child relationship for the text node
    text_node.relationships[NodeRelationship.CHILD] = img_rnis
    # Set the prev node to the current one
    prev_node = text_node
    
    # Add all the nodes on the page to all_nodes
    all_nodes.append(text_node)
    all_nodes.extend(img_nodes)

In [141]:
# Corrsponds to the total no of text+image nodes
len(all_nodes)

1621

### Serialize all nodes

In [144]:
# """ Serialze all the nodes
# """
# with open(f"data_interm_storage/{SRC_TYPE}/nodes_semantic_double.pkl", "wb") as pfile :
#     pickle.dump(nodes, pfile)
    
# with open(f"data_interm_storage/{SRC_TYPE}/nodes_hierarchial.pkl", "wb") as pfile :
#     pickle.dump(hierarchical_nodes, pfile)

# with open(f"data_interm_storage/{SRC_TYPE}/all_nodes.pkl", "wb") as pfile :
#     pickle.dump(all_nodes, pfile)

In [19]:
with open(f"data_interm_storage/{SRC_TYPE}/nodes_semantic_double.pkl", "rb") as pfile :
    semantic_nodes = pickle.load(pfile)
    
with open(f"data_interm_storage/{SRC_TYPE}/nodes_hierarchial.pkl", "rb") as pfile :
    hierarchical_nodes = pickle.load(pfile)
    
with open(f"data_interm_storage/{SRC_TYPE}/all_nodes.pkl", "rb") as pfile :
    all_nodes = pickle.load(pfile)

leaf_nodes = get_leaf_nodes(hierarchical_nodes)

print(f"semantic_nodes: {len(semantic_nodes)}")
print(f"hierarchial_nodes: {len(hierarchical_nodes)}")
print(f"all_nodes: {len(all_nodes)}")
print(f"leaf_nodes: {len(leaf_nodes)}")

semantic_nodes: 1264
hierarchial_nodes: 5660
all_nodes: 1621
leaf_nodes: 4758


## 2) Put into respective data stores

In [20]:
if not os.path.isdir("./gist_onnx") :
    OptimumEmbedding.create_and_save_optimum_model(
        "avsolatorio/GIST-Embedding-v0", "./gist_onnx", export_kwargs={'trust_remote_code': True}
    )
embed_model = OptimumEmbedding(
    folder_name="./gist_onnx"
)

In [21]:
custom_schema = IndexSchema.from_dict(
    {
        "index": {"name": "school_data_auto_bm25", "prefix": "school_doc"},
        # customize fields that are indexed
        "fields": [
            # required fields for llamaindex
            {"type": "tag", "name": "id"},
            {"type": "tag", "name": "doc_id"},
            {"type": "text", "name": "text"},
            # custom vector field for bge-small-en-v1.5 embeddings
            {
                "type": "vector",
                "name": "vector",
                "attrs": {
                    "dims": 768,
                    "algorithm": "hnsw",
                    "distance_metric": "cosine",
                },
            },
        ],
    }
)

In [22]:
redis_client = Redis.from_url("redis://localhost:6379")

In [23]:
vector_store = RedisVectorStore(
    schema=custom_schema,
    redis_client=redis_client,
)

14:08:32 redisvl.index.index INFO   Index already exists, not overwriting.


### a) Put nodes for QnA search into stores

In [24]:
auto_docstore = RedisDocumentStore.from_host_and_port(
    "localhost", 6379, namespace="document_store_auto"
)
bm25_docstore = RedisDocumentStore.from_host_and_port(
    "localhost", 6379, namespace="document_store_bm25"
)

In [25]:
print(len(auto_docstore.docs.items()))
print(len(bm25_docstore.docs.items()))

5660
1264


In [26]:
hierarchical_nodes[0].metadata

{'chapter': 'Chapter1',
 'subject': 'Mathematics',
 'grade': '8th Standard',
 'post_title': 'Chapter 1',
 'post_description': 'The notes for chapter 1 has been uploaded',
 'course_info': '8th Standard Mathematics',
 'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/mathematics/hemh101.pdf',
 'file_name': 'hemh101.pdf',
 'file_type': 'application/pdf',
 'file_size': 1233342,
 'creation_date': '2024-10-31',
 'last_modified_date': '2024-10-31',
 'doc_type': 'Text'}

In [27]:
# # add all nodes to docstore
# print("Adding all hierarchial nodes")
# auto_docstore.add_documents(hierarchical_nodes)
# print("Adding all regular nodes")
# bm25_docstore.add_documents(semantic_nodes)

In [28]:
auto_storage_context = StorageContext.from_defaults(docstore=auto_docstore, vector_store=vector_store)

In [29]:
# auto_index = VectorStoreIndex(
#     leaf_nodes,
#     storage_context=auto_storage_context,
#     embed_model=embed_model
# )

In [30]:
auto_index = VectorStoreIndex.from_vector_store(
    vector_store=vector_store,
    embed_model=embed_model
)

### b) Put nodes for word-for-word search into store

In [31]:
wfw_docstore = RedisDocumentStore.from_host_and_port(
    "localhost", 6379, namespace="all_nodes"
)

In [32]:
len(wfw_docstore.docs.items())

1621

In [33]:
""" Adding all nodes to docstore
"""
# # print("Adding all nodes to docstore")
# wfw_docstore.add_documents(all_nodes)

' Adding all nodes to docstore\n'

# V) Setup Retrievers and Query Engine

## 1) Initialize the Retrievers

### a) For QnA retrieval

In [34]:
bm25_retriever = BM25Retriever.from_defaults(
    docstore=bm25_docstore,
    similarity_top_k=5,
)

In [35]:
base_retriever = auto_index.as_retriever(similarity_top_k=5)
auto_retriever = AutoMergingRetriever(base_retriever, auto_storage_context, verbose=True)

In [36]:
""" Tesing auto merging retriever
"""
query_str = "What is reproduction?"
retrieved_nodes = auto_retriever.retrieve(query_str)

for node in retrieved_nodes:
    display_source_node(node, source_length=5000)

**Node ID:** 8110d263-18bb-4ef2-b0dc-a0afceaca1e6<br>**Similarity:** 0.654238820076<br>**Text:** Migration is the movement of people in and out of an area. Births and deaths are the natural causes of population change. The difference between the birth rate and the death rate of a country is called the natural growth rate. The population increase in the world is mainly due to a rapid increase in the natural growth rate.<br>

**Node ID:** f182cd2d-dc47-4900-926d-433c1643d11f<br>**Similarity:** 0.652929663658<br>**Text:** It's as if women are meant to be made of something different from men altogether, made from dust from earth or rock or rusted iron, whereas you and your lives are made from the purest gold." ... "You're asking me what I mean.<br>

**Node ID:** 534eb5ea-541d-4384-8748-633d991a92bf<br>**Similarity:** 0.6509549617770001<br>**Text:** The population increase in the world is mainly due to a rapid increase in the natural growth rate.

Fig 5.3: World Population Growth<br>

**Node ID:** 73b5b134-7260-484b-a5f5-efe23563024c<br>**Similarity:** 0.650944292545<br>**Text:** It increased at the rate of 5% p.a. Find the population at the end of the year 2000.

Solution: There is 5% increase in population every year, so every new year has a new population. Thus, we can say it is increasing in compounded form.<br>

**Node ID:** 41f91d55-9ae8-4589-97c8-adba65b2b327<br>**Similarity:** 0.650526225567<br>**Text:** Population Decrease  Population Steady  Population Increase

Birth Rate  Birth Rate  Death Rate  Death Rate  Death Rate  Birth Rate  Birth rate more than death rate: population increases. Birth rate and death rate are the same: population stays the same. Death rate more than birth rate: population decreases.<br>

In [37]:
""" Tesing bm25 retriever
"""
query_str = "What is pollination?"
retrieved_nodes = bm25_retriever.retrieve(query_str)

for node in retrieved_nodes:
    display_source_node(node, source_length=5000)

**Node ID:** 0eca3590-558b-4e5c-a59a-c1c5daad4bfb<br>**Similarity:** 4.269379138946533<br>**Text:** Is it to attract insects? Water. Insects visit flowers and carry away pollen on their bodies. Some of the pollen lands on the stigma of a flower of the same kind. The transfer of pollen from the anther to the stigma of a flower (a) is called pollination. If the pollen lands (b) on the stigma of the same flower or another flower of the same plant, it is called self-pollination. When the pollen of a flower lands on the stigma of a flower of a different plant of the same kind, it is called cross-pollination [Fig.<br>

**Node ID:** 750ef717-0455-4835-bae9-57e808ba550f<br>**Similarity:** 2.7358949184417725<br>**Text:** 8.7 Reproduction through spore formation in fungus

REPRODUCTION IN PLANTS 85


Activity 8.4: Male and female unisexual flowers may be present in the same plant or in different plants. Take a mustard/China rose/petunia flower and separate its reproductive parts. Study the various parts of a stamen and pistil. Anther contains pollen grains which produce male gametes. A pistil consists of stigma, style, and ovary. Ovary contains one or more ovules. The female gamete or the egg is formed in an ovule [Fig. 8.9 (b)]. In sexual reproduction, a male and a female gamete fuse to form a zygote. Boojho wants to know how the male gamete in the pollen grain reaches the female gamete present in the ovule. Filament Pollination Generally, pollen grains have a tough protective coat which prevents them from drying up. Since pollen grains are light, they can be carried by wind or insects. Flowers which contain either only pistil or only stamens are called unisexual flowers. Flowers which contain both stamens and pistil are called bisexual flowers. Corn, papaya, and cucumber produce unisexual flowers, whereas mustard, rose, and petunia have bisexual flowers. Both male gamete in the pollen grain reaches the female gamete present in the ovule. Fig. 8.9 Reproductive parts
Fig. 8.10 Pollination in flower


Boojho wants to know why flowers are generally so colourful and fragrant.<br>

**Node ID:** dfabf53c-772f-4bff-9775-b7ae92ce4ba7<br>**Similarity:** 1.463865876197815<br>**Text:** l Where is the fox? l How did it happen? l What is the fox thinking? l Who is the visitor? l What does she want to know? l What is the fox's reply? l What happens next? l Where is the goat? l Where is the fox now? l What is the goat thinking?<br>

**Node ID:** 5d22bbb3-9d98-43e3-a527-3a50e3a46841<br>**Similarity:** 1.254267692565918<br>**Text:** (a) What is the minimum interior angle possible for a regular polygon? Why? (b) What is the maximum exterior angle possible for a regular polygon?<br>

**Node ID:** 71a9735d-268f-4153-b48c-d92b36d7ed08<br>**Similarity:** 1.1815235614776611<br>**Text:** 4. “I could feel his anguish.” What could be the anguish? 5. What endeared the scientist to the writer so that he said he was looking at one of the most beautiful men in the world? 6. Read aloud the description of ‘the beautiful’ man. Which is the most beautiful sentence in the description?<br>

In [38]:
fusion_retriever = QueryFusionRetriever(
    [auto_retriever, bm25_retriever],
    similarity_top_k=3,
    num_queries=4,  # set this to 1 to disable query generation
    mode="reciprocal_rerank",
    use_async=True,
    verbose=True,
)

In [39]:
""" Testing fusion retriever
"""
query_str = "What is the definition of pollination?"
retrieved_nodes = fusion_retriever.retrieve(query_str)

for node in retrieved_nodes:
    display_source_node(node, source_length=5000)

Generated queries:
Here are three search queries related to the input query:
What is the process of pollination in plants and how does it occur?
Types of pollination: self-pollination vs cross-pollination vs artificial pollination
Importance of pollination in ecosystems and its impact on food production


**Node ID:** e48be09a-df7a-4256-a3c0-f23ac120c607<br>**Similarity:** 0.05<br>**Text:** Some of the pollen lands on the stigma of a flower of the same kind. The transfer of pollen from the anther to the stigma of a flower (a) is called pollination. If the pollen lands (b) on the stigma of the same flower or another flower of the same plant, it is called self-pollination.<br>

**Node ID:** 0eca3590-558b-4e5c-a59a-c1c5daad4bfb<br>**Similarity:** 0.05<br>**Text:** Is it to attract insects? Water. Insects visit flowers and carry away pollen on their bodies. Some of the pollen lands on the stigma of a flower of the same kind. The transfer of pollen from the anther to the stigma of a flower (a) is called pollination. If the pollen lands (b) on the stigma of the same flower or another flower of the same plant, it is called self-pollination. When the pollen of a flower lands on the stigma of a flower of a different plant of the same kind, it is called cross-pollination [Fig.<br>

**Node ID:** 20fe6049-a591-4ee9-bd03-5e4c7a7c9106<br>**Similarity:** 0.048915917503966164<br>**Text:** When the pollen of a flower lands on the stigma of a flower of a different plant of the same kind, it is called cross-pollination [Fig. 8.10 (a) and (b)]. The zygote develops into an embryo.<br>

### b) For word-for-word retrieval

In [40]:
all_node_ids = list(wfw_docstore.docs.keys())
len(all_node_ids)

1621

In [41]:
def get_nodes_by_meta(filter_metadata) :
    filtered_nodes = []
    for node_id in all_node_ids:
        node = wfw_docstore.get_node(node_id)
        filter_conditions = [node.metadata.get(key) == value for key, value in filter_metadata.items()]
        if all(filter_conditions) :
            filtered_nodes.append(node)
    
    # Sort the nodes by page number
    filtered_nodes = sorted(filtered_nodes, key=lambda node: (node.metadata["chapter"], node.metadata["page_number"]))
            
    return filtered_nodes

In [42]:
filtered_nodes = get_nodes_by_meta(
    {
        "subject": "English",
        "chapter": "Chapter1",
        "doc_type": "Text"
    }
)
# # Sort nodes in page number order
# doc_nodes = sorted(filtered_nodes, key=lambda node: (node.metadata["chapter"], node.metadata["page_number"]))

In [43]:
filtered_nodes[0].metadata

{'chapter': 'Chapter1',
 'subject': 'English',
 'grade': '8th Standard',
 'post_title': 'Chapter 1',
 'post_description': 'The notes for chapter 1 have been uploaded',
 'course_info': '8th Standard English',
 'file_path': '/home/jovanzac/Jovan/OfflineProjects/Python/Machine_learning/RAG/Iris/ipynb_files/8_grade_texts/English/hehd101.pdf',
 'file_name': 'hehd101.pdf',
 'file_type': 'application/pdf',
 'file_size': 2528583,
 'creation_date': '2024-10-31',
 'last_modified_date': '2024-10-31',
 'page_number': 1,
 'doc_type': 'Text'}

In [44]:
for doc in filtered_nodes :
    print(doc.metadata["page_number"])
    print(doc.text, end="\n"+"*"*100+"\n")

1
Before you read, there are some dates or periods of time in the history of the world that are so significant that everyone knows and remembers them. The story you will read mentions one such date and event: a war between the British and the Germans in 1914. Can you guess which war it was? Do you know which events the dates below refer to? (a) 4 July 1776, (b) 17 December 1903, (c) 6 August 1945, (d) 30 January 1948, (e) 12 April 1961, (f) 20 July 1969. The answers are on page 23.

I spotted it from a a junk shop in Bridport, a roll-top desk. The man said it was early nineteenth century, and oak. It was going for a high price, but I thought it was selling for very little money because it was in a bad condition, the roll-top in several pieces, one leg clumsily mended, scorch marks all down one side. I thought I could restore it. It would be a risk, a challenge, but I had to have it. I paid the man and brought it back to my workroom at the back of the garage. I began work on it on Chris

## 2) Query Engine

### a) For QnA

In [45]:
query_engine = RetrieverQueryEngine.from_args(fusion_retriever, llm=Settings.llm)

In [46]:
qna_prompt_str = """
Context information is below.
---------------------
{context_str}
---------------------
Given the context information and not prior knowledge, answer the query. 
Make the response as descriptive as possible, including all relevant contexts provided.
Do not format the response in any way.
Query: {query_str}
Answer:
"""

In [47]:
new_qa_prompt = PromptTemplate(
    qna_prompt_str
)
QA_PROMPT_KEY = "response_synthesizer:text_qa_template"
# Overriding default prompt template for the query engine
query_engine.update_prompts(
    {QA_PROMPT_KEY: new_qa_prompt}
)

In [48]:
query_str = "What is the definition of pollination?"

response = query_engine.query(query_str)
response.response

Generated queries:
Here are three search queries related to the input query:
What is the process of pollination in plants and how does it occur?
Types of pollination: self-pollination vs cross-pollination vs artificial pollination
Importance of pollination in agriculture and ecosystem health


'According to the provided context, pollination is defined as the transfer of pollen from the anther to the stigma of a flower. This process occurs when pollen from the anther of a flower is carried away by insects or other means and lands on the stigma of the same or another flower of the same kind, allowing for fertilization to take place.'

# VI) ReAct agent

## 1) The tool functions

### a) For QnA

In [1]:
def rag_agent(user_query) :
    """Function to respond to user's questions and academic queries"""
    print(f"Responding to te user query: {user_query}")
    
    response = query_engine.query(user_query)
    return response.response.strip()
    
#     return "The query has been successfully answered"

rag_tool = FunctionTool.from_defaults(
    fn=rag_agent,
    description= (
        "Used to respond to the user's questions and academic queries"
        "Must be used to respond to any general question, query or doubt the user has on any academic subject or topic"
        "Used for QnA type question answering."
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'user_query': 'What is photosynthesis?'}})"
    )
)

NameError: name 'FunctionTool' is not defined

In [ ]:
rag_agent("What is photosynthesis?")

### b) Generate response for Word-forWord retrieval

In [51]:
def number_to_ordinal(n):
    if 10 <= n % 100 <= 20:  # Handle special case for teens
        suffix = "th"
    else:
        suffix = {1: "st", 2: "nd", 3: "rd"}.get(n % 10, "th")
    return f"{n}{suffix}"

In [52]:
def read_textbook(subject, chapter, num_pgs=3, include_imgs=False) :
    """Function to read out a textbook to the student"""
    print("In read_textbook")
    text_nodes = get_nodes_by_meta(
        {
            "subject": subject,
            "chapter": chapter,
            "doc_type": "Text"
        }
    )
    
    if include_imgs :
        img_nodes = get_nodes_by_meta(
            {
                "subject": subject,
                "chapter": chapter,
                "doc_type": "Image"
            }
        )
    else :
        img_nodes = []
    
    response = ""
    for node in text_nodes[:num_pgs] :
        pg_no = node.metadata["page_number"]
        response += f"\n\nStarting page {pg_no}..\n\n"
        response += node.text + "\n\n"
        if img_nodes :
            response += "\nThere are {num_imgs} images in page {pg_no}\n\n"

            img_count = 0
            while img_nodes[0].metadata["page_number"] == pg_no :
                img_count += 1
                response += f"The {number_to_ordinal(img_count)} image is:\n"
                response += img_nodes[0].text + "\n\n"
                img_nodes.pop(0)

            response = response.format(
                num_imgs = img_count,
                pg_no = pg_no
            )
        
        response += f"This is the end of page {pg_no}\n"
    
        
    return str(response)

In [2]:
print(read_textbook("Science", "Chapter10", num_pgs=3, include_imgs=True))

NameError: name 'read_textbook' is not defined

In [54]:
wfw_tool = FunctionTool.from_defaults(
    fn=read_textbook,
    description=(
        "Used to read out textbooks or certain parts of textbooks"
        "If the user query mentions keywords like 'read-out', 'read for me' or something similar, this tool is used"
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'subject': 'English', 'chapter': 'Chapter1', 'num_pgs': 3, 'include_imgs': False}})"
    )
)

### c) For Quiz mode

In [55]:
quiz_sys_prompt = """
## INSTRUCTIONS
You are a quiz master whose sole responsibility is to create a set of **random multiple-choice questions (MCQs)** based on the context provided in the section titled "CONTEXT." 
The purpose of these questions is to test the user's knowledge of the subject comprehensively.

Try to ask questions on different subjects and include as much variety as possible. Questions must come from
different themes and topics in the context as far as possible.

You are to generate exactly {num_qns} questions based only on the provided context. 
The generated questions and options must strictly follow the format specified in the section titled "OUTPUT FORMAT."


### RULES
1. Do NOT include any text or explanation other than what is explicitly specified in "OUTPUT FORMAT".
2. Ensure all generated questions are strictly related to the "CONTEXT" and avoid introducing external information.
3. The questions should vary in type (e.g., conceptual, factual, or application-based) to test a range of understanding.
4. Each question must have exactly four options. Ensure that:
   - Only **one option is correct**.
   - The other three options are plausible yet incorrect.
5. The difficulty level of the questions should be balanced across the set (easy, moderate, and challenging).
6. The numbering of questions must range from 1 to {num_qns}.


### OUTPUT FORMAT
[
    {{
        "question_no": <Question number from 1 to {num_qns}>,
        "question": <A relevant question based on the provided context>,
        "option1": <The first option>,
        "option2": <The second option>,
        "option3": <The third option>,
        "option4": <The fourth option>,
        "correct_option": <The correct option from "option1", "option2", "option3", or "option4">
    }},
]

### CONTEXT
{context_str}
"""

In [56]:
def generate_quiz_qns(subject, chapter, num_qns=10) :
    """Function to create a set of random MCQ quiz/test questions"""
    print("In generate_quiz_qns")
    text_nodes = get_nodes_by_meta(
        {
            "subject": subject,
            "chapter": chapter,
            "doc_type": "Text"
        }
    )
    
    context_str = "\n\n".join([node.text for node in text_nodes])
    
    prompt = quiz_sys_prompt.format(
        context_str=context_str,
        num_qns=num_qns
    )
    start_time = time.time()
    llm_response = Settings.llm.complete(prompt).text
    end_time = time.time()
    elapsed_time = end_time - start_time
    print(f"The LLm call took {elapsed_time:.4f} seconds to run.")
    
    # Extracting the questions from the response
    pattern = r'\{\s*"question_no".*?\}'
    matches = re.findall(pattern, llm_response, re.DOTALL)
    print(matches)
    questions = [json.loads(match) for match in matches]
    
    return questions, llm_response, matches

In [57]:
start_time = time.time()
questions, llm_response, matches = generate_quiz_qns("Science", "Chapter3")
display(questions)
end_time = time.time()
elapsed_time = end_time - start_time
print(f"The code took {elapsed_time:.4f} seconds to run.")

In generate_quiz_qns
The LLm call took 3.4802 seconds to run.
['{\n        "question_no": 1,\n        "question": "What is the purpose of a clinical thermometer?",\n        "option1": "To measure the temperature of any object",\n        "option2": "To measure the temperature of the human body only",\n        "option3": "To measure the temperature of hot milk",\n        "option4": "To measure the temperature of the surroundings",\n        "correct_option": "option2"\n    }', '{\n        "question_no": 2,\n        "question": "Why should we not use a clinical thermometer to measure the temperature of hot milk?",\n        "option1": "Because it is not designed for that purpose",\n        "option2": "Because it is not accurate",\n        "option3": "Because it is too expensive",\n        "option4": "Because it is too big",\n        "correct_option": "option1"\n    }', '{\n        "question_no": 3,\n        "question": "What is the range of a clinical thermometer?",\n        "option1": "Fro

[{'question_no': 1,
  'question': 'What is the purpose of a clinical thermometer?',
  'option1': 'To measure the temperature of any object',
  'option2': 'To measure the temperature of the human body only',
  'option3': 'To measure the temperature of hot milk',
  'option4': 'To measure the temperature of the surroundings',
  'correct_option': 'option2'},
 {'question_no': 2,
  'question': 'Why should we not use a clinical thermometer to measure the temperature of hot milk?',
  'option1': 'Because it is not designed for that purpose',
  'option2': 'Because it is not accurate',
  'option3': 'Because it is too expensive',
  'option4': 'Because it is too big',
  'correct_option': 'option1'},
 {'question_no': 3,
  'question': 'What is the range of a clinical thermometer?',
  'option1': 'From -10°C to 110°C',
  'option2': 'From 35°C to 42°C',
  'option3': 'From 0°C to 100°C',
  'option4': 'From -20°C to 50°C',
  'correct_option': 'option2'},
 {'question_no': 4,
  'question': 'What is the proc

The code took 3.8448 seconds to run.


In [58]:
quiz_tool = FunctionTool.from_defaults(
    fn=generate_quiz_qns,
    description=(
        "Used to create a quiz/test on a particular chapter of a subject"
        "If the user query mentions keywords like 'quiz', 'test' or something similar, this tool is used"
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'subject': 'English', 'chapter': 'Chapter1', 'num_qns': 10}})"
    )
)

### d) Other "hooks" 

In [59]:
def send_mail(to, body) :
    """Function to send mail"""
    print(f"Sending Mail to {to} with the body:\n {body}")
    return "Your mail has been successfully sent"

send_mail_tool = FunctionTool.from_defaults(
    fn=send_mail,
    description= (
        "Used to send emails."
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'to': 'Sarat', 'body': 'Hey, how are you?'}})"
    )
)

In [60]:
def retrieve_mail() :
    """Function to retrieve all unread mails"""
    print(f"Retrieving all mails")
    return "Your mails have ben retrieved"

ret_mail_tool = FunctionTool.from_defaults(
    fn=retrieve_mail,
    description= (
        "Used to retrieve all unread mails."
    )
)

In [61]:
def send_telegram(to, body) :
    """Function to send a telegram message"""
    print(f"Sending telegram message to {to} with the body:\n {body}")
    return "Your telegram message has been successfully sent"

send_telegram_tool = FunctionTool.from_defaults(
    fn=send_telegram,
    description= (
        "Used to send messages to contacts on telegram."
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'to': 'Sarat', 'body': 'Hey, how are you?'}})"
    )
)

In [62]:
def retrieve_telegram() :
    """Function to retrieve all unread telegram messages"""
    print(f"Retrieving all telegram mesages")
    return "Your telegram messages have been retrieved"

ret_telegram_tool = FunctionTool.from_defaults(
    fn=retrieve_telegram,
    description= (
        "Used to retrieve all unread messages on telegram."
    )
)

In [63]:
def send_whatsapp(to, body) :
    """Function to send a whatsapp message"""
    print(f"Sending whatsapp message to {to} with the body:\n {body}")
    return "Your whatsapp message has been successfully sent"

send_whatsapp_tool = FunctionTool.from_defaults(
    fn=send_whatsapp,
    description= (
        "Used to send messages to contacts on whatsapp."
        "The input to the tool should be in a JSON format representing the kwargs (e.g. {{'to': 'Sarat', 'body': 'Hey, how are you?'}})"
    )
)

## 1) Old method using builtin ReAct agents

In [83]:
react_tools = [
    send_whatsapp_tool,
    rag_tool,
    send_mail_tool,
    ret_mail_tool,
    send_telegram_tool,
    ret_telegram_tool,
    wfw_tool
]

In [60]:
agent = ReActAgent.from_tools(
    tools=react_tools,
    llm=Settings.llm,
    memory=False,
    verbose=True
)

In [61]:
response = agent.chat("Read out chapter 3 of English?")
print(response)

> Running step 5a6765ac-b546-4632-991f-3adfda501e08. Step input: Read out chapter 3 of English?
Thought: The current language of the user is: English. I need to use a tool to help me answer the question.
Action: read_textbook
Action Input: {'subject': 'English', 'chapter': 'Chapter3', 'num_pgs': 3, 'include_imgs': False}
In read_textbook
Observation: 

Starting page 1..

Before you read, here are some pictorial glimpses of the history of our country from 1757 to 1857. These pictures and 'speech bubbles' will help clarify your understanding of the conditions that led to the event known as the First War of Independence in 1857.

At a function in Delhi:

1. The Martyrs: Oh, my countrymen! Let your eyes fill with tears as you recall the sacrifices of India's martyrs.

This is the end of page 1


Starting page 2..

2. The Company's conquests (1757-1849)

With its superior weapons, the East India Company was extending its power in 18th century India. The British Indian princes were short-sig

## 2) Custom workflow

In [64]:
class DefaultMode(BaseModel) :
    name: str = "Default"

In [65]:
class QnAMode(BaseModel) :
    name: str = "QnA"
    response: str = ""
    mode_has_been_set: bool = False

In [66]:
class ReaderMode :
    name: str = "Reader"
    response: str = ""
    mode_has_been_set: bool = False

In [67]:
# Initializing the Quiz engine
class QuizMode(BaseModel) :
    name: str = "Quiz"
    user_response: str = ""
    quiz_qns: List[Dict] = []
    num_qns: int = 0
    remaining_qns: int = 0
    mode_has_been_set: bool = False

In [68]:
class InputEvent(Event):
    input: list[ChatMessage]


class ToolCallEvent(Event):
    id: str
    name: str
    params: dict
        

class ToolResponseEvent(Event) :
    tool_response: ChatMessage
        

class ToolResponseEventQuiz(Event) :
    mode: QuizMode

In [69]:
class QuizInputEvent(Event) :
    start: bool = False
    end: bool = False
    user_response: str = ""

        
class QuizPostEvalEvent(Event) :
    start: bool = False
    end: bool = False
        

class QuizEndEvent(Event) :
    response: str = ""
    end: bool = False

In [70]:
def no_tool_required_func() :
    """ Used when no tool is required to be chosen, as the user did not ask for
    the use of any
    """
    print("In no _tool_required")
    return None

In [71]:
no_tool_required = FunctionTool.from_defaults(
    fn=no_tool_required_func,
    description=(
        "Used when the user's query does not explicitly specify us to use any of the other tools."
        "This tool is to be preferred over the others unless the user's query implies otherwise."
    )
)

In [72]:
sys_prompt = """
## INSTRUCTIONS
You are the Iris, the great AI assistant that helps out
students in their educationsal needs.

You are given a set of modes/tools to choose from. Based on the descriptions provided
for each tool and the user's query, choose the tool that you deem most appropriate.

You must strictly follow all the specified rules when deciding which mode to choose.

### RULES
- Read the descripton for each mode carefully before choosing one
- You must only select ANY ONE mode


## Available Modes/Tools
- Mode names: {mode_names}
- Mode descriptions: {mode_desc}
"""

In [73]:
hook_sys_prompt = """
## INSTRUCTIONS
You are given a set of tools to choose from. Based in the descriptions provided
for each tool and the user's query, choose the tool that you deem most appropriate.

You must strictly follow all the specified rules when deciding which tool to choose.

Unless the user query explicitly mentions or implies that a specific task must be done
that requires the use of one of the provided tools, the tool no_tool_required must
always be the preferred choice.

### RULES
- Read the descripton for each mode carefully before choosing one
- You must only select ANY ONE tool

## Available Tools
- Tool names: {tool_names}
- Tool descriptions: {tool_desc}
"""

In [74]:
class Hooks(Workflow):
    def __init__(
        self,
        *args: any,
        llm: Groq,
        tools: list[FunctionTool],
        timeout: int = 20,
        react_system_prompt: str = """
            ## Available Tools
            - Tool names: {tool_names}
            - Tool descriptions: {tool_desc}
        """
    ):
        super().__init__(*args)
        self._timeout = timeout
        self.llm = llm
        self.tools = tools
        
        self.get_tool = {tool.metadata.get_name(): tool for tool in self.tools}
        # initialize chat history/memory with system prompt
        self.react_system_prompt = react_system_prompt
        self.sys_msg = ChatMessage(
            role=MessageRole.SYSTEM,
            content=self.react_system_prompt.format(
                tool_desc="\n  ".join([f"{tool.metadata.name}: {tool.metadata.description}" for tool in self.tools]),
                tool_names=", ".join([tool.metadata.name for tool in self.tools])
            )
        )
        self.memory = ChatMemoryBuffer.from_defaults(llm=llm)
        
        
    @step
    async def prepare_chat_history(self, ev: StartEvent) -> InputEvent:
        print("(HOOK)In prepare chat history")
        # Clear memory
        self.memory.reset()
        self.memory.put(message=self.sys_msg)
        
        # Add the given input history to chat history
        chat_history = ev.input
#         for message in chat_history:
#             if 'additional_kwargs' in message.__dict__:
#                 message.additional_kwargs.pop('tool_call_id', None)
#                 message.additional_kwargs.pop('name', None)
            
#         for message in chat_history:
#             self.memory.put(message)
        
        current_chat_history = self.memory.get()
        # return input event
        return InputEvent(input=current_chat_history)
    
    
    @step
    async def handle_llm_input(self, ev: InputEvent) -> ToolCallEvent | StopEvent:
        print("\n(HOOK)In handle llm_input")
        chat_history = ev.input
        
        # get llm response on hook selection
        response = await self.llm.achat_with_tools(
            tools=self.tools,
            chat_history=chat_history,
            tool_choice="required",
        )
        # add response to chat history / memory
        self.memory.put(message=response.message)
        # get tool calls
        tool_calls = self.llm.get_tool_calls_from_response(
            response
        )
        print(f"(HOOK)Tool chosen: {tool_calls[-1].tool_name}")
        
        if tool_calls[-1].tool_name == "no_tool_required_func":
            return StopEvent(result={"response": None})
        
        else :
            # return tool call event
            return ToolCallEvent(
                id=tool_calls[-1].tool_id,
                name=tool_calls[-1].tool_name,
                params=tool_calls[-1].tool_kwargs,
            )
    
    
    @step
    async def run_tool(self, ev: ToolCallEvent) -> StopEvent:
        print("(HOOK)In Run tool")
        tool_name = ev.name
        additional_kwargs = {
            "tool_call_id": ev.id,
            "name": tool_name
        }
        # get chosen tool
        tool = self.get_tool.get(tool_name)
        if not tool:
            tool_msg = ChatMessage(
                role="tool",
                content=f"Tool {tool_name} not found",
                additional_kwargs=additional_kwargs
            )
        else:
#             # now call tool
#             tool_output = await tool.acall(**ev.params)
            tool_output = tool.call(**ev.params)
            print("*"*100)
            print(f"(HOOK)tool output:\n{tool_output.content}")
            print("*"*100)
            tool_msg = ChatMessage(
                role="tool",
                content=tool_output.content,
                additional_kwargs=additional_kwargs
            )
        self.memory.put(message=tool_msg)
        chat_history = self.memory.get()
        
        return StopEvent(result={"response": tool_msg.content})

In [75]:
class QuizFlow(Workflow):
    def __init__(
        self,
        *args: any,
        llm: Groq,
        timeout: int = 20
    ):
        super().__init__(*args)
        self._timeout = timeout
        self.llm = llm
        
        self.score = 0

    @staticmethod
    def format_quiz_qn(quiz_qn, include_instructions=False) :
        qn_str = (
        "\tThis is question number {qn_no}:\n\n"
        
        "\t{question}\n\n"
        
        "\tYour options are:\n\n"
        
        "\t Option1 is: {option1}\n"
        "\t Option2 is: {option2}\n"
        "\t Option3 is: {option3}\n"
        "\t Option4 is: {option4}\n\n"
        
        "\tPlease respond with your answer when you are ready\n"
        )
        
        qn_str = qn_str.format(
            qn_no=quiz_qn["question_no"],
            question=quiz_qn["question"],
            option1=quiz_qn["option1"],
            option2=quiz_qn["option2"],
            option3=quiz_qn["option3"],
            option4=quiz_qn["option4"],
        )
        
        if include_instructions :
            instructions = (
            "\n\n\tThe quiz is about to begin. You will soon enter quiz mode and will not be able to exit until it completes.\n"
            "\tYour instructions are:\n\n"
            "\t - There are {num_qns} questions in this test\n"
            "\t - The final grade will be out of {num_qns}\n"
            "\t - The test will be mutiple choice. Listen to each question before answering.\n"
            "\t - Your response should be either 'option1', 'option2', 'option3' or 'option4'.\n\n\n"
            )
            
            
            response = instructions + qn_str
            
        else :
            response = qn_str
        
        return response
    
    
    @staticmethod
    def return_user_score(score, num_qns) :
        return (
        "\tCongrats! You have successfully completed the quiz.\n"
        "\tYou have scored {score} out of {num_qns}!\n"
        "\tExiting quiz mode now..\n"
        ).format(
            score = score,
            num_qns = num_qns
        )


    @step
    async def recieve_user_input(self, ev: StartEvent) -> QuizInputEvent:
        self.mode = ev.mode
        user_response = self.mode.user_response
        
        start, end = False, False
        if self.mode.num_qns == self.mode.remaining_qns :
            start = True
            
            return QuizPostEvalEvent(
                start = start
            )

        elif self.mode.remaining_qns <= 0 :
            end = True
        
        return QuizInputEvent(
            start = start,
            end = end,
            user_response = user_response
        )
    

    @step
    async def evaluate_user_response(self, ev: QuizInputEvent) -> QuizEndEvent | QuizPostEvalEvent:
        user_response = ev.user_response
        
        # To extract the specified option number from the response
        mapping = {
            "1": 1, "one": 1,
            "2": 2, "two": 2,
            "3": 3, "three": 3,
            "4": 4, "four": 4
        }
        
        pattern = r'\boption\s*(?:1|2|3|4|one|two|three|four)\b'
        matches = re.findall(pattern, user_response, flags=re.IGNORECASE)
        
        if not matches :
            return QuizEndEvent(
                response = "Sorry, I could not understand your choice. Please try again."
            )
        else :
            ans = matches[0].lower()
            key = re.sub(r'\s+', '', ans.split('option')[1]).lower()
            if key in mapping :
                option_no = mapping[key]
                
        prev_qn_index = self.mode.num_qns - self.mode.remaining_qns - 1
        prev_qn_ans = self.mode.quiz_qns[prev_qn_index]["correct_option"]
        if prev_qn_ans.lower() == f"option{option_no}" :
            self.score += 1
        
        if ev.end :
            return QuizEndEvent(
                end = True
            )

        else :
            return QuizPostEvalEvent(
                start = ev.start
            )


    @step
    async def get_quiz_qn(self, ev: QuizPostEvalEvent) -> QuizEndEvent:
        qn_index = self.mode.num_qns - self.mode.remaining_qns
        quiz_qn = self.mode.quiz_qns[qn_index]
        
        question_str = self.format_quiz_qn(quiz_qn, include_instructions=ev.start)
        if ev.start :
            question_str = question_str.format(
                num_qns = self.mode.num_qns
            )
        
        return QuizEndEvent(
            response = question_str,
            end = False
        )
        
    
    @step
    async def final_response(self, ev: QuizEndEvent) -> StopEvent:
        if ev.end :
            return StopEvent(
                result = {"response": self.return_user_score(self.score, self.mode.num_qns)}
            )
        
        else :
            return StopEvent(
                result = {"response": ev.response}
            )

In [76]:
class IrisFlow(Workflow):
    def __init__(
        self,
        *args: any,
        llm: Groq,
        tools: list[FunctionTool],
        hooks_agent: Workflow,
        quiz_agent: Workflow,
        timeout: int = 20,
        react_system_prompt: str = """
            ## Available Modes/Tools
            - Mode names: {mode_names}
            - Mode descriptions: {mode_desc}
        """
    ):
        super().__init__(*args)
        self._timeout = timeout
        self.llm = llm
        self.tools = tools
        
        self.hooks_agent = hooks_agent
        self.quiz_agent = quiz_agent
        
        self.get_tool = {tool.metadata.get_name(): tool for tool in self.tools}
        # initialize chat history/memory with system prompt
        self.react_system_prompt = react_system_prompt
        self.sys_msg = ChatMessage(
            role=MessageRole.SYSTEM,
            content=self.react_system_prompt.format(
                mode_desc="\n  ".join([f"{tool.metadata.name}: {tool.metadata.description}" for tool in self.tools]),
                mode_names=", ".join([tool.metadata.name for tool in self.tools])
            )
        )
        self.memory = ChatMemoryBuffer.from_defaults(llm=llm)
        
        self.mode = DefaultMode()

        
    @staticmethod
    def combine_res(mode_res, hook_res) :
        res = f"Your answer is: {mode_res} \n\nAn additional step was also performed: \n{hook_res}"
        
        return res


    @step
    async def prepare_chat_history(self, ev: StartEvent) -> InputEvent:
        print("In prepare chat history")
        # clear memory
        self.memory.reset()
        self.memory.put(message=self.sys_msg)
        
        # get user input
        user_input = ev.input
        user_msg = ChatMessage(role="user", content=user_input)
        self.memory.put(message=user_msg)
        
        # get chat history
        chat_history = self.memory.get()
        # return input event
        return InputEvent(input=chat_history)


    @step
    async def handle_llm_input(self, ev: InputEvent) -> ToolCallEvent | ToolResponseEventQuiz:
        print("\nIn handle llm_input")
        chat_history = ev.input
        
        if self.mode.name == "Quiz" :
            user_response = [msg.content for msg in chat_history if msg.role == "user"][-1]
            self.mode.user_response = user_response
            
            return ToolResponseEventQuiz(
                mode = self.mode
            )
            
        # get llm response on mode selection
        response = await self.llm.achat_with_tools(
            tools=self.tools,
            chat_history=chat_history,
            tool_choice="required",
        )
        # add response to chat history / memory
        self.memory.put(message=response.message)
        # get tool calls
        tool_calls = self.llm.get_tool_calls_from_response(
            response
        )
        print(f"Tool chosen: {tool_calls[-1].tool_name}")
        
        if tool_calls[-1].tool_name == "rag_agent" :
            self.mode = QnAMode()
        
        elif tool_calls[-1].tool_name == "read_textbook" :
            self.mode = ReaderMode()
        
        elif tool_calls[-1].tool_name == "generate_quiz_qns" :
            self.mode = QuizMode()
        
        # return tool call event
        return ToolCallEvent(
            id=tool_calls[-1].tool_id,
            name=tool_calls[-1].tool_name,
            params=tool_calls[-1].tool_kwargs,
        )


    @step
    async def run_tool(self, ev: ToolCallEvent) -> ToolResponseEvent | ToolResponseEventQuiz:
        print("In Run tool")
        print(f"Tool identified: {ev.name}")
        tool_name = ev.name
        additional_kwargs = {
            "tool_call_id": ev.id,
            "name": tool_name
        }
        # get chosen tool
        tool = self.get_tool.get(tool_name)
        if not tool:
            tool_msg = ChatMessage(
                role="tool",
                content=f"Tool {tool_name} not found",
                additional_kwargs=additional_kwargs
            )
        else:
            # now call tool
#             tool_output = await tool.acall(**ev.params)
            start_time = time.time()
            tool_output = tool.call(**ev.params)
            end_time = time.time()
            elapsed_time = end_time - start_time
            print(f"The tool call took {elapsed_time:.4f} seconds to run.")
            
            # If the mode is quiz, then start the quiz engine and continue the flow accordingly
            if self.mode.name == "Quiz" :
#                 tool_content = tool_output.content.replace("'", '"')
#                 tool_content = json.loads(tool_content)
                tool_content = tool_output.raw_output
                print(f"tool_content: {tool_content}")
                self.mode.quiz_qns = tool_content
                self.mode.num_qns = len(tool_content)
                self.mode.remaining_qns = self.mode.num_qns
                self.mode_has_been_set = True
                
                return ToolResponseEventQuiz(
                    mode = self.mode
                )
                
            tool_msg = ChatMessage(
                role="tool",
                content=tool_output.content,
                additional_kwargs=additional_kwargs
            )
        self.memory.put(message=tool_msg)
        
        return ToolResponseEvent(tool_response=tool_msg)


    @step
    async def apply_hooks(self, ev: ToolResponseEvent) -> StopEvent:
        # Get the current complete chat history
        chat_history = self.memory.get()
        # Remove the system prompt before passing it onto the hook decider
        chat_history.pop(0)
        # Run the hook agent on the user query
        res = await self.hooks_agent.run(input=chat_history)
#         res = {"response": None}
        
        if res["response"] == None :
            response = ev.tool_response.content
    
        else :
            response = self.combine_res(ev.tool_response.content, res["response"])

        self.mode.response = response
        self.mode.mode_has_been_set = True
        
        self.mode = DefaultMode()
        
        return StopEvent(result={"response": response})
        
    
    @step
    async def quiz_engine(self, ev: ToolResponseEventQuiz) -> StopEvent:
        mode = ev.mode
        
        res = await self.quiz_agent.run(mode=mode)
        
        if res["response"][:5].lower() != "sorry" :
            self.mode.remaining_qns -= 1
        if self.mode.remaining_qns == -1 :
            self.mode = DefaultMode()
        
        return StopEvent(result={"response": res["response"]})

In [77]:
tools = [
    send_whatsapp_tool,
    send_mail_tool,
    ret_mail_tool,
    send_telegram_tool,
    ret_telegram_tool,
    no_tool_required
]

In [78]:
modes = [
    rag_tool,
    wfw_tool,
    quiz_tool
]

In [86]:
hooks = Hooks(
    llm=groq_text_llm,
    tools=tools,
    timeout=200,
    react_system_prompt=hook_sys_prompt
)

In [87]:
quiz_agent = QuizFlow(
    timeout=200,
    llm=groq_text_llm
)

In [88]:
agent = IrisFlow(
    llm=groq_text_llm,
    tools=modes,
    hooks_agent=hooks,
    quiz_agent=quiz_agent,
    timeout=600,
    react_system_prompt=sys_prompt
)

In [89]:
start_time = time.time()
res = await agent.run(input="Create a quiz on chapter 3 of english")
end_time = time.time()
elapsed_time = end_time - start_time
print(f"The entire agent took {elapsed_time:.4f} seconds to run.")
print(res["response"])

In prepare chat history

In handle llm_input
Tool chosen: generate_quiz_qns
In Run tool
Tool identified: generate_quiz_qns
In generate_quiz_qns
The LLm call took 25.3999 seconds to run.
['{\n        "question_no": 1,\n        "question": "What was the main reason for the East India Company\'s conquests in 18th century India?",\n        "option1": "The British wanted to spread their religion in India.",\n        "option2": "The British Indian princes were short-sighted and sought their help.",\n        "option3": "The East India Company wanted to establish a democratic government in India.",\n        "option4": "The British wanted to free India from the Mughal Empire.",\n        "correct_option": "option2"\n    }', '{\n        "question_no": 2,\n        "question": "What was the impact of the British policies on Indian industries?",\n        "option1": "They helped Indian industries to flourish.",\n        "option2": "They had no impact on Indian industries.",\n        "option3": "They 

TypeError: list indices must be integers or slices, not str

# VII) Text-To-Speech (TTS)

## 1) Google Cloud TTS

In [85]:
from google.cloud import texttospeech

os.environ["GOOGLE_APPLICATION_CREDENTIALS"] = "iris_service_acc_voice.json"

# Instantiates a client
client = texttospeech.TextToSpeechClient()

text = """
Google Cloud Text-to-Speech enables developers to synthesize natural-sounding speech with
100+ voices, available in multiple languages and variants. It applies DeepMind’s groundbreaking
research in WaveNet and Google’s powerful neural networks to deliver the highest fidelity
possible. As an easy-to-use API, you can create lifelike interactions with your users, across
many applications and devices.
"""

# Set the text input to be synthesized
synthesis_input = texttospeech.SynthesisInput(text=text)

# Refer https://cloud.google.com/text-to-speech/docs/voices
# To get list of all available voices
voice = texttospeech.VoiceSelectionParams(
    language_code="ml-IN",
    name="ml-IN-Standard-A"
)

# Configure audio
audio_config = texttospeech.AudioConfig(
    audio_encoding=texttospeech.AudioEncoding.MP3,
)

# Synthesize speech
response = client.synthesize_speech(
    input=synthesis_input, voice=voice, audio_config=audio_config
)
     
# The response's audio_content is binary.
# with open("output.mp3", "wb") as out:
#     # Write the response to the output file.
#     out.write(response.audio_content)
#     print('Audio content written to file "output.mp3"')

PermissionDenied: 403 This API method requires billing to be enabled. Please enable billing on project #941996505023 by visiting https://console.developers.google.com/billing/enable?project=941996505023 then retry. If you enabled billing for this project recently, wait a few minutes for the action to propagate to our systems and retry. [reason: "BILLING_DISABLED"
domain: "googleapis.com"
metadata {
  key: "service"
  value: "texttospeech.googleapis.com"
}
metadata {
  key: "containerInfo"
  value: "941996505023"
}
metadata {
  key: "consumer"
  value: "projects/941996505023"
}
, locale: "en-US"
message: "This API method requires billing to be enabled. Please enable billing on project #941996505023 by visiting https://console.developers.google.com/billing/enable?project=941996505023 then retry. If you enabled billing for this project recently, wait a few minutes for the action to propagate to our systems and retry."
, links {
  description: "Google developers console billing"
  url: "ht

In [662]:
from IPython.display import Audio

Audio(response.audio_content)